# Ventas Horizontal 

In [1]:
# ============================================================
# LIBRERÍAS
# ============================================================
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import scipy.stats as stats
from statsmodels.tsa.stattools import acf
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.impute import SimpleImputer
from sklearn.linear_model import Ridge
from sklearn.model_selection import TimeSeriesSplit, cross_val_score
from IPython.display import display
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score


def EDA_master(df_input):
    """
    Realiza un Análisis Exploratorio de Datos (EDA) exhaustivo para series temporales.
    
    Argumentos:
    df_input -- DataFrame de pandas. La col 0 debe ser fecha, el resto numéricas.
    
    Retorna:
    dict -- Diccionario con estadísticas clave, outliers detectados y metadatos por columna.
    """
    
    # -------------------------------------------------------------------------
    # 1. VALIDACIONES INICIALES Y PREPROCESAMIENTO ROBUSTO
    # -------------------------------------------------------------------------
    print("--- INICIO DE AUDITORÍA DE DATOS ---")
    df = df_input.copy()
    resultados_export = {}
    
    # Validación Columna 0: Fecha
    col_fecha = df.columns[0]
    conversion_msg = "Original"
    
    if col_fecha != "Fecha":
        print(f"⚠️ Aviso: La primera columna se llama '{col_fecha}', se renombrará a 'Fecha'.")
        df.rename(columns={col_fecha: "Fecha"}, inplace=True)
    
    if not pd.api.types.is_datetime64_any_dtype(df["Fecha"]):
        try:
            df["Fecha"] = pd.to_datetime(df["Fecha"])
            conversion_msg = "Corregido a datetime"
        except Exception as e:
            raise ValueError(f"❌ Error crítico: La columna 1 no se pudo convertir a fecha. {e}")

    # Ordenamiento Cronológico
    df = df.sort_values(by="Fecha").reset_index(drop=True)
    orden_msg = "Sí (Se aplicó sort)"
    
    # Detección de Duplicados en Fecha
    duplicados = df["Fecha"].duplicated().sum()
    if duplicados > 0:
        print(f"⚠️ Advertencia: Se encontraron {duplicados} fechas duplicadas. Se mantendrá el último registro.")
        df = df.drop_duplicates(subset="Fecha", keep="last").reset_index(drop=True)
    
    print(f"✅ Validación Estructural:\n   - Fecha: {conversion_msg}\n   - Ordenado: {orden_msg}\n   - Duplicados eliminados: {duplicados}")
    
    # Validación de Columnas Numéricas
    cols_numericas = df.columns[1:]
    if len(cols_numericas) == 0:
        raise ValueError("❌ Error: No hay columnas de datos numéricos para analizar.")
        
    for col in cols_numericas:
        if not pd.api.types.is_numeric_dtype(df[col]):
            raise TypeError(f"❌ Error: La columna '{col}' no es numérica.")
            
        nulos = df[col].isnull().sum()
        fechas_nulas = df.loc[df[col].isnull(), "Fecha"].dt.strftime('%Y-%m-%d').tolist()
        nulos_msg = f"Valores nulos: {nulos}"
        if nulos > 0:
            nulos_msg += f" | Fechas: {fechas_nulas[:3]}..." if len(fechas_nulas) > 3 else f" | Fechas: {fechas_nulas}"
        
        print(f"   - Columna '{col}': Numérica ✓ | {nulos_msg}")

    print("-" * 60)

    # -------------------------------------------------------------------------
    # CICLO DE ANÁLISIS POR COLUMNA
    # -------------------------------------------------------------------------
    for col in cols_numericas:
        print(f"\n📊 ANALIZANDO SERIE: {col.upper()}")
        serie = df[col].dropna() # Trabajamos sin nulos para stats
        fechas_serie = df.loc[serie.index, "Fecha"]
        
        # --- 2. ESTADÍSTICAS DESCRIPTIVAS E INTERPRETACIÓN ---
        desc = serie.describe()
        
        # Extracción de fechas de max/min
        idx_max = serie.idxmax()
        fecha_max = df.loc[idx_max, "Fecha"].strftime('%Y-%m-%d')
        val_max = serie.max()
        
        idx_min = serie.idxmin()
        fecha_min = df.loc[idx_min, "Fecha"].strftime('%Y-%m-%d')
        val_min = serie.min()
        
        media = serie.mean()
        mediana = serie.median()
        std_dev = serie.std()
        cv = std_dev / media if media != 0 else 0 # Coeficiente de variación
        
        interpretacion_dispersion = "alta" if cv > 0.2 else "baja" # Regla de dedo: CV > 20% es alta dispersión
        
        print(f"   🔹 Rango: Máximo de {val_max:,.2f} ({fecha_max}) | Mínimo de {val_min:,.2f} ({fecha_min})")
        print(f"   🔹 Centralidad: Media {media:,.2f} | Mediana {mediana:,.2f} (Diferencia: {((media-mediana)/mediana)*100:.1f}%)")
        print(f"   🔹 Volatilidad: Desviación {std_dev:,.2f} (Dispersión {interpretacion_dispersion}, CV={cv:.1%})")

        # --- 3. ANÁLISIS DE DISTRIBUCIÓN Y NORMALIDAD ---
        # Test Shapiro-Wilk (si N > 3, si no, no tiene sentido)
        if len(serie) > 3:
            stat_shapiro, p_value = stats.shapiro(serie)
            es_normal = p_value > 0.05
            tipo_dist = "Normal (Gaussiana)" if es_normal else "No Normal (Probable sesgo o outliers)"
            print(f"   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value={p_value:.4f} -> {tipo_dist}")
        
        # Histograma + KDE
        fig_dist = make_subplots(rows=2, cols=1, shared_xaxes=True, 
                                 vertical_spacing=0.03, row_heights=[0.15, 0.85])
        
        # Boxplot arriba (para ver outliers rápido)
        fig_dist.add_trace(go.Box(x=serie, name="Boxplot", boxpoints='outliers', marker_color='#636EFA'), row=1, col=1)
        
        # Histograma abajo
        fig_dist.add_trace(go.Histogram(x=serie, name="Frecuencia", nbinsx=20, marker_color='#EF553B', opacity=0.7), row=2, col=1)
        
        fig_dist.update_layout(title=f"Distribución de {col} ({tipo_dist})", 
                               height=400, showlegend=False, template="plotly_white")
        fig_dist.show()

        # --- 4. DETECCIÓN DE OUTLIERS (IQR) ---
        Q1 = serie.quantile(0.25)
        Q3 = serie.quantile(0.75)
        IQR = Q3 - Q1
        lim_inf = Q1 - 1.5 * IQR
        lim_sup = Q3 + 1.5 * IQR
        
        outliers = df[(df[col] < lim_inf) | (df[col] > lim_sup)]
        num_outliers = len(outliers)
        
        print(f"   🔹 Outliers detectados (Método IQR): {num_outliers}")
        if num_outliers > 0:
            print(f"     Fechas clave: {outliers['Fecha'].dt.date.tolist()}")

        # --- 5. GRÁFICA PRINCIPAL DE SERIE TEMPORAL ---
        # Promedio móvil (Tendencia)
        df['MA_4'] = df[col].rolling(window=4).mean()
        
        fig_main = go.Figure()
        
        # Serie original
        fig_main.add_trace(go.Scatter(x=df['Fecha'], y=df[col], mode='lines+markers', 
                                      name='Real', line=dict(color='#1f77b4', width=2)))
        
        # Tendencia
        fig_main.add_trace(go.Scatter(x=df['Fecha'], y=df['MA_4'], mode='lines', 
                                      name='Tendencia (MA-4)', line=dict(color='#ff7f0e', dash='dash')))
        
        # Outliers visuales
        if num_outliers > 0:
            fig_main.add_trace(go.Scatter(x=outliers['Fecha'], y=outliers[col], mode='markers',
                                          name='Outliers', marker=dict(color='red', size=10, symbol='x')))

        # Anotaciones Max/Min
        fig_main.add_annotation(x=df.loc[idx_max, "Fecha"], y=val_max, text=f"Máx: {val_max:.1f}", showarrow=True, arrowhead=1)
        fig_main.add_annotation(x=df.loc[idx_min, "Fecha"], y=val_min, text=f"Mín: {val_min:.1f}", showarrow=True, arrowhead=1, ay=30)
        
        fig_main.update_layout(title=f"Evolución Temporal: {col}", xaxis_title="Fecha", yaxis_title="Valor", 
                               template="plotly_white", hovermode="x unified")
        fig_main.show()

        # --- 6. GRÁFICA DE CAMBIOS PERIÓDICOS (%) ---
        # Calculamos % de cambio
        df['pct_change'] = df[col].pct_change() * 100
        colors = ['#2ca02c' if x >= 0 else '#d62728' for x in df['pct_change']]
        
        ultimo_cambio = df['pct_change'].iloc[-1]
        
        fig_var = go.Figure()
        fig_var.add_trace(go.Bar(x=df['Fecha'], y=df['pct_change'], marker_color=colors, name="% Var"))
        
        fig_var.add_hline(y=0, line_dash="solid", line_color="black", annotation_text="Base 0%")
        fig_var.update_layout(title=f"Variación Porcentual Periodo a Periodo ({col})", 
                              yaxis_title="% Variación", template="plotly_white")
        
        # Anotación último periodo
        label_cambio = "Positivo" if ultimo_cambio >= 0 else "Negativo"
        print(f"   🔹 Dinámica Reciente: Último cambio de {ultimo_cambio:+.1f}% ({label_cambio})")
        fig_var.show()

        # --- 7. AUTOCORRELACIÓN (ACF) ---
        # Calculamos ACF con statsmodels
        lags = min(12, len(serie)//2 - 1) # Máximo 12 lags o la mitad de la serie
        acf_vals, confint = acf(serie, nlags=lags, alpha=0.05)
        # El lag 0 siempre es 1, lo quitamos para ver mejor la estacionalidad
        acf_vals = acf_vals[1:]
        conf_interval = 1.96 / np.sqrt(len(serie)) # Aprox intervalo de confianza
        
        x_lags = list(range(1, lags + 1))
        
        fig_acf = go.Figure()
        # Barras de correlación
        fig_acf.add_trace(go.Bar(x=x_lags, y=acf_vals, width=0.2, marker_color='black', name='Autocorrelación'))
        # Intervalos de confianza (Zona de ruido)
        fig_acf.add_shape(type="rect", x0=0.5, x1=lags+0.5, y0=-conf_interval, y1=conf_interval,
                          fillcolor="blue", opacity=0.2, line_width=0)
        
        fig_acf.update_layout(title=f"Autocorrelación (ACF) - Detección de Patrones ({col})", 
                              xaxis_title="Lags (Periodos atrás)", yaxis_title="Correlación", 
                              yaxis_range=[-1, 1], template="plotly_white")
        fig_acf.show()
        
        # Interpretación básica
        lags_significativos = [i+1 for i, val in enumerate(acf_vals) if abs(val) > conf_interval]
        print(f"   🔹 Memoria de la serie: Lags significativos en {lags_significativos} (Patrones repetitivos)")

        # Guardar resultados en diccionario
        resultados_export[col] = {
            "estadisticas": desc.to_dict(),
            "outliers_indices": outliers.index.tolist(),
            "maximo": {"fecha": fecha_max, "valor": val_max},
            "minimo": {"fecha": fecha_min, "valor": val_min},
            "trend_ultimo_cambio_pct": ultimo_cambio,
            "es_normal": es_normal
        }

    return resultados_export

# ============================================================
# SANITY CHECKS + PREPARACIÓN
# ============================================================
def preparar_df(df: pd.DataFrame, target: str = "Absorción") -> pd.DataFrame:
    df = df.copy()
    if "Fecha" not in df.columns:
        raise ValueError("El DataFrame debe contener la columna 'Fecha'.")
    df["Fecha"] = pd.to_datetime(df["Fecha"], errors="coerce")
    df = df.sort_values("Fecha").reset_index(drop=True)

    if target not in df.columns:
        raise ValueError(f"No se encontró la columna target '{target}'.")

    # Mantén Fecha como columna (no index)
    return df

# ============================================================
# GRÁFICO INTERACTIVO DOBLE EJE (Absorción vs variable seleccionable)
# ============================================================
def plot_absorcion_vs_variable(
    df: pd.DataFrame,
    target: str = "Absorción",
    default_var: str | None = None,
    titulo: str = "Absorción vs Variable Seleccionada (Doble Eje)"
) -> go.Figure:
    df = df.copy()
    df["Fecha"] = pd.to_datetime(df["Fecha"], errors="coerce")
    df = df.sort_values("Fecha").reset_index(drop=True)

    # Variables numéricas candidatas
    numeric_cols = df.select_dtypes(include=[np.number]).columns.tolist()
    candidates = [c for c in numeric_cols if c != target]

    if not candidates:
        raise ValueError("No hay variables numéricas (además del target) para comparar.")

    if default_var is None or default_var not in candidates:
        default_var = candidates[0]

    fig = go.Figure()

    # Trace 0: Absorción (SIEMPRE en y1)
    fig.add_trace(
        go.Scatter(
            x=df["Fecha"],
            y=df[target],
            name=target,
            mode="lines+markers",
            yaxis="y"   # y1
        )
    )

    # Trace 1: Variable dinámica (SIEMPRE en y2)
    fig.add_trace(
        go.Scatter(
            x=df["Fecha"],
            y=df[default_var],
            name=default_var,
            mode="lines+markers",
            yaxis="y2"
        )
    )

    # Dropdown: SOLO cambia la traza 1 (índice 1)
    buttons = []
    for var in candidates:
        buttons.append(
            dict(
                label=var,
                method="restyle",
                args=[
                    {"y": [df[var].tolist()], "name": [var]},  # cambia SOLO y y name
                    [1]  # índice de la traza dinámica
                ]
            )
        )

    fig.update_layout(
        title=titulo,
        xaxis=dict(title="Fecha"),

        # y1 (izquierda) = Absorción
        yaxis=dict(title=target),

        # y2 (derecha) = variable dinámica
        yaxis2=dict(
            title=default_var,
            overlaying="y",
            side="right",
            showgrid=False
        ),

        hovermode="x unified",
        legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="left", x=0),

        updatemenus=[
            dict(
                type="dropdown",
                direction="down",
                x=1.02, y=1.15,
                xanchor="left", yanchor="top",
                buttons=buttons,
                showactive=True
            )
        ],
        margin=dict(l=60, r=70, t=90, b=50)
    )

    # Opcional: también actualizar el título de y2 cuando cambias dropdown
    # (Plotly no lo hace automáticamente con "restyle", así que lo resolvemos con un truco:
    # lo dejamos fijo o actualizamos manualmente si lo integras en Dash/Streamlit.)
    return fig

# ============================================================
# EDA MULTIVARIABLE (JUPYTER)
# - Imprime resultados + interpretación automática
# - Muestra gráficas (Plotly) para validar visualmente
# - NO guarda resultados (no retorna nada)
# ============================================================

# -----------------------------
# Helpers: interpretación automática
# -----------------------------
def _interpret_corr(valor: float) -> str:
    """Interpretación tipo 'analista senior' para correlación (Pearson/Spearman/Kendall)."""
    if pd.isna(valor):
        return "Sin dato (NaN)."
    if valor >= 0.85:
        return "Fuerte positiva: relación muy sólida. Posible driver clave."
    elif valor >= 0.50:
        return "Moderada positiva: relación relevante. Investigar causalidad/segmentación."
    elif valor >= 0.20:
        return "Débil positiva: señal marginal. No es driver principal."
    elif valor > -0.20:
        return "Cerca de 0: sin relación clara (puede ser no lineal o ruido)."
    elif valor > -0.50:
        return "Débil negativa: fricción ligera sobre el target."
    elif valor > -0.85:
        return "Moderada negativa: impacto importante (p.ej. sobreoferta/costo)."
    else:
        return "Fuerte negativa: factor crítico que frena el mercado."


def _interpret_nonlinearity(p: float, s: float, k: float, thr: float = 0.25) -> str:
    """Detecta posible no linealidad comparando métodos de correlación."""
    if any(pd.isna(x) for x in [p, s, k]):
        return "No evaluable (NaN)."
    d_ps = abs(p - s)
    d_pk = abs(p - k)
    if d_ps > thr or d_pk > thr:
        return "Probable relación NO lineal/monótona. Considera transformaciones (log/dif) o modelos no lineales."
    return "Relación aproximadamente lineal (Pearson ≈ Spearman/Kendall)."


def _interpret_vif(vif: float) -> str:
    if pd.isna(vif):
        return "No evaluable (pocos datos/columna constante)."
    if np.isinf(vif):
        return "PROBLEMA: multicolinealidad extrema (VIF infinito). Elimina/combina variables."
    if vif < 5:
        return "OK: baja multicolinealidad (variable relativamente independiente)."
    if vif < 10:
        return "Cuidado: multicolinealidad moderada. Revisa redundancia."
    return "PROBLEMA: multicolinealidad alta. Elimina una variable del grupo o crea índice compuesto."


def _interpret_cov(valor: float) -> str:
    """Covarianza depende de escala: interpretamos solo dirección."""
    if pd.isna(valor):
        return "Sin dato (NaN)."
    if valor > 0:
        return "Positiva: tienden a moverse en la misma dirección (suben/bajan juntas)."
    if valor < 0:
        return "Negativa: una tiende a subir cuando la otra baja."
    return "Cero: no hay co-movimiento lineal aparente."


def _interpret_volatility(std_pct: float) -> str:
    """Std del % change: thresholds heurísticos (ajústalos según tu industria)."""
    if pd.isna(std_pct):
        return "Sin dato (NaN)."
    if std_pct >= 30:
        return "Muy volátil: explica shocks/eventos; mala para tendencia estable."
    if std_pct >= 15:
        return "Volatilidad media: sensible a ciclos; útil para timing."
    return "Estable: buena para explicar tendencia estructural."


# -----------------------------
# Helpers: cálculo VIF (sin statsmodels)
# -----------------------------
def _calc_vif(df_num: pd.DataFrame, target: str) -> pd.DataFrame:
    """
    VIF sin statsmodels:
      Xi ~ X_others  => R^2
      VIF = 1 / (1 - R^2)
    """
    X = df_num.drop(columns=[target], errors="ignore").copy()
    X = X.dropna(axis=1, how="all")

    # Quitamos filas con NaN para VIF (si quedan pocas, VIF no es confiable)
    X = X.dropna(axis=0)

    if X.shape[1] == 0:
        return pd.DataFrame(columns=["variable", "VIF"])

    if X.shape[1] == 1:
        return pd.DataFrame({"variable": X.columns, "VIF": [np.nan]})

    lr = LinearRegression()
    rows = []

    for col in X.columns:
        y = X[col].values
        X_others = X.drop(columns=[col]).values

        # Evitar crash por muy pocos datos
        if len(y) < 6 or X_others.shape[1] == 0:
            rows.append((col, np.nan))
            continue

        # Si y es constante, R^2 no es informativo
        if np.nanstd(y) < 1e-9:
            rows.append((col, np.nan))
            continue

        lr.fit(X_others, y)
        r2 = lr.score(X_others, y)
        if r2 >= 0.999999:
            vif = np.inf
        else:
            vif = 1.0 / (1.0 - r2)
        rows.append((col, vif))

    return pd.DataFrame(rows, columns=["variable", "VIF"]).sort_values("VIF", ascending=False).reset_index(drop=True)


# -----------------------------
# FUNCIÓN PRINCIPAL: imprime + gráficas + interpretación
# -----------------------------
def analisis_estadistico(
    df: pd.DataFrame,
    target: str = "Absorción",
    corr_threshold: float = 0.40,
    vif_threshold: float = 5.0,
    top_n_pairs: int = 12,
    top_n_scatter: int = 6,
    show_heatmaps: bool = True,
    show_scatter: bool = True
) -> None:
    """
    EDA multivariable con interpretación automática (Jupyter).
    NO retorna nada: imprime tablas + interpretaciones y muestra gráficas Plotly.
    """

    # ============================================================
    # 0) Preparación / sanity
    # ============================================================
    df = df.copy()
    if "Fecha" not in df.columns:
        raise ValueError("El DataFrame debe contener columna 'Fecha'.")
    df["Fecha"] = pd.to_datetime(df["Fecha"], errors="coerce")
    df = df.sort_values("Fecha").reset_index(drop=True)

    if target not in df.columns:
        raise ValueError(f"No existe la columna target '{target}'.")

    df_num = df.select_dtypes(include=[np.number]).copy()
    if target not in df_num.columns:
        raise ValueError(f"'{target}' debe ser numérico para este análisis.")

    if len(df) < 8:
        print("⚠️ Advertencia: muy pocos registros. Las métricas pueden ser inestables.")

    # ============================================================
    # 1) Correlaciones: Pearson / Spearman / Kendall
    # ============================================================
    corr_p = df_num.corr(method="pearson")
    corr_s = df_num.corr(method="spearman")
    corr_k = df_num.corr(method="kendall")

    corr_target = pd.DataFrame({
        "Pearson": corr_p[target],
        "Spearman": corr_s[target],
        "Kendall": corr_k[target],
    })
    corr_target["|Pearson|"] = corr_target["Pearson"].abs()
    corr_target = corr_target.sort_values("|Pearson|", ascending=False)

    # ============================================================
    # 2) Covarianza / varianza
    # ============================================================
    cov = df_num.cov()
    varianza = df_num.var().sort_values(ascending=False).to_frame("Varianza")

    # ============================================================
    # 3) Variación % y volatilidad
    # ============================================================
    variacion_pct = df_num.pct_change() * 100.0
    volatilidad_pct = variacion_pct.std().sort_values(ascending=False).to_frame("Std_%Cambio")

    # ============================================================
    # 4) VIF
    # ============================================================
    vif_df = _calc_vif(df_num, target=target)

    # ============================================================
    # 5) IMPRESIÓN + INTERPRETACIÓN AUTOMÁTICA
    # ============================================================
    print("\n" + "=" * 95)
    print("REPORTE EDA MULTIVARIABLE (con interpretación automática)")
    print("=" * 95)
    print(f"Registros: {len(df)} | Variables numéricas: {df_num.shape[1]}")
    print(f"Rango fechas: {df['Fecha'].min().date()} a {df['Fecha'].max().date()}")
    print("-" * 95)

    # ----------------------------
    # A) Correlación vs target (tabla)
    # ----------------------------
    print("\nA) CORRELACIONES VS TARGET (Pearson / Spearman / Kendall)")
    display(corr_target.round(3))

    print("\nA.1) Interpretación automática (por variable vs target)")
    for var in corr_target.index:
        if var == target:
            continue
        p = float(corr_target.loc[var, "Pearson"])
        s = float(corr_target.loc[var, "Spearman"])
        k = float(corr_target.loc[var, "Kendall"])

        interp_p = _interpret_corr(p)
        interp_s = _interpret_corr(s)
        interp_k = _interpret_corr(k)
        interp_shape = _interpret_nonlinearity(p, s, k)

        print(f"\n• {var}")
        print(f"  - Pearson  = {p: .3f} → {interp_p}")
        print(f"  - Spearman = {s: .3f} → {interp_s}")
        print(f"  - Kendall  = {k: .3f} → {interp_k}")
        print(f"  - Forma    → {interp_shape}")

    # Alertas por umbral (drivers potenciales)
    print(f"\nA.2) Variables con |Pearson| >= {corr_threshold} (posibles drivers a investigar):")
    drivers = corr_target[(corr_target.index != target) & (corr_target["|Pearson|"] >= corr_threshold)]
    if drivers.empty:
        print("  - Ninguna supera el umbral.")
    else:
        for var in drivers.index:
            p = corr_target.loc[var, "Pearson"]
            signo = "positiva" if p > 0 else "negativa"
            print(f"  - {var}: {signo} (Pearson={p:.2f}) → {_interpret_corr(p)}")

    # ----------------------------
    # B) Multicolinealidad VIF
    # ----------------------------
    print("\n" + "-" * 95)
    print("B) MULTICOLINEALIDAD (VIF)")
    if vif_df.empty:
        print("No hay suficientes variables para calcular VIF.")
    else:
        display(vif_df.round(2))

        print("\nB.1) Interpretación automática VIF")
        for _, r in vif_df.iterrows():
            print(f"• {r['variable']}: VIF={r['VIF']:.2f} → {_interpret_vif(r['VIF'])}")

        print(f"\nB.2) Alertas VIF >= {vif_threshold}")
        high_vif = vif_df[vif_df["VIF"] >= vif_threshold]
        if high_vif.empty:
            print("  - Ninguna supera el umbral.")
        else:
            for _, r in high_vif.iterrows():
                print(f"  - {r['variable']}: VIF={r['VIF']:.2f} → {_interpret_vif(r['VIF'])}")

    # ----------------------------
    # C) Volatilidad (% cambio) y varianza
    # ----------------------------
    print("\n" + "-" * 95)
    print("C) VOLATILIDAD Y VARIANZA (para distinguir shocks vs tendencia)")
    print("\nC.1) Top volatilidad (Std del % cambio)")
    display(volatilidad_pct.head(15).round(2))

    print("\nC.2) Interpretación automática (volatilidad)")
    for var, row in volatilidad_pct.head(10).iterrows():
        stdp = float(row["Std_%Cambio"])
        print(f"• {var}: std%={stdp:.2f} → {_interpret_volatility(stdp)}")

    print("\nC.3) Varianza (nivel)")
    display(varianza.head(15).round(2))
    print("\nNota: varianza depende de escala; úsala para detectar variables con rangos enormes (posibles transformaciones log).")

    # ----------------------------
    # D) Covarianza vs target (dirección, no fuerza)
    # ----------------------------
    print("\n" + "-" * 95)
    print("D) COVARIANZA VS TARGET (dirección del co-movimiento; NO está normalizada)")
    cov_target = cov[target].sort_values(ascending=False).to_frame("Covarianza_con_target")
    display(cov_target.round(2))

    print("\nD.1) Interpretación automática (covarianza vs target)")
    for var, row in cov_target.iterrows():
        if var == target:
            continue
        cv = float(row["Covarianza_con_target"])
        print(f"• {var}: cov={cv:.2f} → {_interpret_cov(cv)}")

    # ============================================================
    # 6) GRÁFICAS (Plotly)
    # ============================================================

    # ----------------------------
    # Heatmaps de correlación
    # ----------------------------
    if show_heatmaps:
        def _heatmap(corr_df: pd.DataFrame, title: str):
            fig = go.Figure(
                data=go.Heatmap(
                    z=corr_df.values,
                    x=corr_df.columns,
                    y=corr_df.index,
                    zmin=-1, zmax=1,
                    colorbar=dict(title="corr")
                )
            )
            fig.update_layout(title=title, height=700)
            fig.show()

        _heatmap(corr_p, "Matriz de correlación (Pearson) — lineal")
        _heatmap(corr_s, "Matriz de correlación (Spearman) — monotónica (robusta)")
        _heatmap(corr_k, "Matriz de correlación (Kendall) — útil con muestra pequeña")

        # Top pares correlacionados (Pearson)
        pairs = []
        cols = list(corr_p.columns)
        for i in range(len(cols)):
            for j in range(i + 1, len(cols)):
                pairs.append((cols[i], cols[j], corr_p.iloc[i, j]))

        df_pairs = pd.DataFrame(pairs, columns=["Var1", "Var2", "Pearson"])
        df_pairs["|Pearson|"] = df_pairs["Pearson"].abs()
        df_pairs = df_pairs.sort_values("|Pearson|", ascending=False).head(top_n_pairs)

        fig_pairs = go.Figure(
            data=go.Bar(
                x=df_pairs["|Pearson|"],
                y=df_pairs["Var1"] + " ↔ " + df_pairs["Var2"],
                orientation="h"
            )
        )
        fig_pairs.update_layout(
            title=f"Top {top_n_pairs} pares más correlacionados (|Pearson|) — posible redundancia / relación fuerte",
            xaxis_title="|Correlación|",
            yaxis_title="Pares",
            height=520
        )
        fig_pairs.show()

        print("\nInterpretación (Top pares):")
        print("• PARES muy altos (|r|>0.85) suelen indicar variables redundantes (ojo en modelado).")
        print("• Si el par incluye el target, puede ser un driver candidato (validar causalidad y rezagos).")

    # ----------------------------
    # VIF barplot
    # ----------------------------
    if not vif_df.empty:
        fig_vif = go.Figure(
            data=go.Bar(
                x=vif_df["VIF"].replace([np.inf], np.nan),
                y=vif_df["variable"],
                orientation="h"
            )
        )
        fig_vif.update_layout(
            title="VIF por variable — multicolinealidad (más alto = más redundante)",
            xaxis_title="VIF",
            yaxis_title="Variable",
            height=620
        )
        fig_vif.show()

        print("\nInterpretación (VIF):")
        print("• VIF<5: OK. | 5–10: revisar. | >10: problema, eliminar/combinar variables.")
        print("• En tu caso (DataTur por estrellas), es normal que muchas salgan con VIF alto: crea índices compuestos.")

    # ----------------------------
    # Volatilidad barplot
    # ----------------------------
    vol = volatilidad_pct.reset_index().rename(columns={"index": "Variable"})
    fig_vol = go.Figure(
        data=go.Bar(
            x=vol["Std_%Cambio"],
            y=vol["Variable"],
            orientation="h"
        )
    )
    fig_vol.update_layout(
        title="Volatilidad: Std del % cambio — (alto = shock/ciclo, bajo = tendencia estable)",
        xaxis_title="std(% cambio)",
        yaxis_title="Variable",
        height=720
    )
    fig_vol.show()

    print("\nInterpretación (Volatilidad):")
    print("• Muy volátil: útil para shocks (inseguridad/eventos), pero puede meter ruido al pronóstico.")
    print("• Estable: útil para tendencia estructural y escenarios de largo plazo.")

    # ----------------------------
    # Scatter target vs top variables (por |Pearson|)
    # ----------------------------
    if show_scatter:
        top_vars = [v for v in corr_target.index if v != target][:top_n_scatter]

        for v in top_vars:
            x = df[v].astype(float).values
            y = df[target].astype(float).values
            mask = ~np.isnan(x) & ~np.isnan(y)

            if mask.sum() < 6:
                continue

            x_m = x[mask]
            y_m = y[mask]

            # Trendline lineal simple para visualizar forma general
            m, b = np.polyfit(x_m, y_m, 1)
            y_hat = m * x_m + b

            fig_sc = go.Figure()
            fig_sc.add_trace(go.Scatter(x=x_m, y=y_m, mode="markers", name="Datos"))
            fig_sc.add_trace(go.Scatter(x=x_m, y=y_hat, mode="lines", name="Tendencia lineal"))

            p = corr_p.loc[target, v]
            s = corr_s.loc[target, v]
            k = corr_k.loc[target, v]

            fig_sc.update_layout(
                title=f"{target} vs {v} | Pearson={p:.2f} | Spearman={s:.2f} | Kendall={k:.2f}",
                xaxis_title=v,
                yaxis_title=target,
                height=480
            )
            fig_sc.show()

            print(f"\nInterpretación (scatter) para '{v}':")
            print(f"• Pearson={p:.2f} → {_interpret_corr(p)}")
            print(f"• Spearman={s:.2f}, Kendall={k:.2f} → {_interpret_nonlinearity(p, s, k)}")
            print("• Si el scatter muestra curvatura/saturación: prueba log(x), diferencias o modelos no lineales.")
            print("• Si sospechas rezago (preventa): prueba correlación con lag (X_{t-1}, X_{t-2}).")

    print("\n" + "=" * 95)
    print("FIN DEL REPORTE")
    print("=" * 95)



def calc_vif_no_statsmodels(df_num: pd.DataFrame, target: str) -> pd.DataFrame:
    X = df_num.drop(columns=[target], errors="ignore").copy()
    X = X.dropna(axis=1, how="all").dropna(axis=0)

    if X.shape[1] == 0:
        return pd.DataFrame(columns=["variable", "VIF"])
    if X.shape[1] == 1:
        return pd.DataFrame({"variable": X.columns, "VIF": [np.nan]})

    lr = LinearRegression()
    rows = []
    for col in X.columns:
        y = X[col].values
        Xo = X.drop(columns=[col]).values

        if len(y) < 6 or Xo.shape[1] == 0 or np.nanstd(y) < 1e-9:
            rows.append((col, np.nan))
            continue

        lr.fit(Xo, y)
        r2 = lr.score(Xo, y)
        vif = np.inf if r2 >= 0.999999 else 1.0 / (1.0 - r2)
        rows.append((col, vif))

    return pd.DataFrame(rows, columns=["variable", "VIF"]).sort_values("VIF", ascending=False).reset_index(drop=True)

# ============================================================
# 1) CONSTRUIR ÍNDICES (ocupación / densidad / estadía / turismo)
# 2) RECALCULAR CORRELACIONES + VIF (ya NO infinitos)
# 3) ENTRENAR MODELO ARX SIMPLE CON REZAGOS y decir qué se sostiene
# ============================================================

def zscore(s: pd.Series) -> pd.Series:
    s = pd.to_numeric(s, errors="coerce")
    mu = s.mean()
    sd = s.std(ddof=0)
    if pd.isna(sd) or sd == 0:
        return s * np.nan
    return (s - mu) / sd

def cols_by_pattern(df: pd.DataFrame, contains: str) -> list[str]:
    return [c for c in df.columns if contains in c]

def safe_row_mean(df: pd.DataFrame, cols: list[str]) -> pd.Series:
    if not cols:
        return pd.Series([np.nan] * len(df), index=df.index)
    return df[cols].apply(pd.to_numeric, errors="coerce").mean(axis=1)


def build_indices(
    df: pd.DataFrame,
    *,
    prefix_pasajeros: str = "Pasajeros_",
    prefix_ocupacion: str = "%_ocupacion_",
    prefix_estadia: str = "Estadia_promedio_",
    prefix_densidad: str = "Densidad_prom_",
    robust: bool = True,
    fillna: bool = True,
) -> pd.DataFrame:
    """
    Construye índices agregados para reducir multicolinealidad:
      - idx_turismo   (desde Pasajeros_*)
      - idx_ocupacion (desde %_ocupacion_*)
      - idx_estadia   (desde Estadia_promedio_*)
      - idx_densidad  (desde Densidad_prom_*)
    
    Qué hace internamente:
      1) Detecta columnas por prefijos (familias).
      2) Convierte a numérico y agrega por periodo.
      3) Normaliza cada familia con z-score (robusto o estándar).
      4) Genera un índice como promedio de z-scores (misma escala).
    
    Nota:
      - Con 16 registros, esta compresión es clave para evitar VIF infinitos.
      - No elimina columnas originales; solo agrega 4 columnas nuevas.
    """
    df = df.copy()

    # -----------------------------
    # 0) Asegurar Fecha (si existe)
    # -----------------------------
    if "Fecha" in df.columns:
        df["Fecha"] = pd.to_datetime(df["Fecha"], errors="coerce")
        df = df.sort_values("Fecha").reset_index(drop=True)

    # -----------------------------
    # Helpers
    # -----------------------------
    def _to_numeric(cols):
        for c in cols:
            df[c] = pd.to_numeric(df[c], errors="coerce")

    def _robust_z(s: pd.Series) -> pd.Series:
        s = pd.to_numeric(s, errors="coerce")
        if robust:
            med = np.nanmedian(s)
            mad = np.nanmedian(np.abs(s - med))
            # Escala MAD -> std aprox (consistente con normal)
            denom = 1.4826 * mad if (mad is not None and mad > 0) else np.nanstd(s)
        else:
            med = np.nanmean(s)
            denom = np.nanstd(s)

        if denom is None or denom == 0 or np.isnan(denom):
            return pd.Series(np.zeros(len(s)), index=s.index)

        return (s - med) / denom

    def _build_index(cols, name):
        if not cols:
            df[name] = np.nan
            return

        _to_numeric(cols)

        # Normaliza cada columna y promedia para el índice
        zmat = []
        for c in cols:
            zmat.append(_robust_z(df[c]))
        Z = pd.concat(zmat, axis=1)
        df[name] = Z.mean(axis=1)

    # -----------------------------
    # 1) Detectar familias por prefijo
    # -----------------------------
    pasajeros_cols = [c for c in df.columns if c.startswith(prefix_pasajeros)]
    ocup_cols      = [c for c in df.columns if c.startswith(prefix_ocupacion)]
    estadia_cols   = [c for c in df.columns if c.startswith(prefix_estadia)]
    densidad_cols  = [c for c in df.columns if c.startswith(prefix_densidad)]

    # -----------------------------
    # 2) Construir índices
    # -----------------------------
    _build_index(pasajeros_cols, "idx_turismo")
    _build_index(ocup_cols,      "idx_ocupacion")
    _build_index(estadia_cols,   "idx_estadia")
    _build_index(densidad_cols,  "idx_densidad")

    # -----------------------------
    # 3) Limpieza opcional
    # -----------------------------
    if fillna:
        # Si algún índice quedó NaN (por falta de columnas), lo rellenamos con 0
        # para no romper VIF/ARX. (0 = "neutro" en z-score)
        for c in ["idx_turismo", "idx_ocupacion", "idx_estadia", "idx_densidad"]:
            if c in df.columns:
                df[c] = df[c].fillna(0.0)

    return df


def corr_and_vif_report(df: pd.DataFrame, target: str, features: list[str]) -> tuple[pd.DataFrame, pd.DataFrame]:
    """
    Recalcula correlaciones y VIF SOLO con un set reducido de features.
    """
    # Correlaciones
    num = df[[target] + features].copy()
    for c in num.columns:
        num[c] = pd.to_numeric(num[c], errors="coerce")
    corr_p = num.corr(method="pearson")
    corr_s = num.corr(method="spearman")
    corr_k = num.corr(method="kendall")

    corr_target = pd.DataFrame({
        "Pearson": corr_p[target],
        "Spearman": corr_s[target],
        "Kendall": corr_k[target],
    }).drop(index=target, errors="ignore")
    corr_target["|Pearson|"] = corr_target["Pearson"].abs()
    corr_target = corr_target.sort_values("|Pearson|", ascending=False)

    # VIF
    vif_df = calc_vif_no_statsmodels(num.dropna(axis=0), target=target)

    return corr_target, vif_df


def train_arx_simple(
    df: pd.DataFrame,
    target: str,
    exog_features: list[str],
    lags_y: int = 1,
    lags_x: int = 1,
    ridge_alpha: float = 1.0,
    n_splits: int = 4
) -> dict:
    """
    ARX simple:
      y_t ~ y_{t-1..t-lags_y} + X_{t-1..t-lags_x}

    Regresa:
      - tabla de coeficientes (en escala estandarizada)
      - RMSE CV (time series)
      - fit sobre todo el dataset (por transparencia)
    """
    data = df.copy()
    data = data.sort_values("Fecha").reset_index(drop=True)

    # Ensurar numérico
    data[target] = pd.to_numeric(data[target], errors="coerce")
    for f in exog_features:
        data[f] = pd.to_numeric(data[f], errors="coerce")

    # Construir lags
    feat_cols = []
    for i in range(1, lags_y + 1):
        col = f"{target}_lag{i}"
        data[col] = data[target].shift(i)
        feat_cols.append(col)

    for f in exog_features:
        for i in range(1, lags_x + 1):
            col = f"{f}_lag{i}"
            data[col] = data[f].shift(i)
            feat_cols.append(col)

    # Drop rows sin lags
    model_df = data[["Fecha", target] + feat_cols].dropna().reset_index(drop=True)

    X = model_df[feat_cols]
    y = model_df[target]

    # Pipeline robusta
    model = Pipeline(steps=[
        ("imputer", SimpleImputer(strategy="median")),
        ("scaler", StandardScaler()),
        ("reg", Ridge(alpha=ridge_alpha))
    ])

    # CV temporal
    tscv = TimeSeriesSplit(n_splits=min(n_splits, max(2, len(model_df)//3)))
    scores = cross_val_score(model, X, y, cv=tscv, scoring="neg_root_mean_squared_error")
    rmse_cv = float((-scores).mean())

    # Fit final (en todo el set usable)
    model.fit(X, y)
    y_hat = model.predict(X)
    rmse_fit = float(np.sqrt(mean_squared_error(y, y_hat)))
    r2_fit = float(r2_score(y, y_hat))

    # Coeficientes (en espacio estandarizado)
    coef = model.named_steps["reg"].coef_
    coef_df = pd.DataFrame({"feature": feat_cols, "coef": coef}).sort_values("coef", key=lambda s: s.abs(), ascending=False).reset_index(drop=True)

    # Interpretación “qué se sostiene”
    # (magnitudes relativas; con pocos datos no usar p-values)
    coef_df["impacto"] = pd.cut(
        coef_df["coef"].abs(),
        bins=[-np.inf, 0.15, 0.35, np.inf],
        labels=["débil", "moderado", "fuerte"]
    )

    return {
        "model_df": model_df,
        "features_used": feat_cols,
        "coef_df": coef_df,
        "rmse_cv": rmse_cv,
        "rmse_fit": rmse_fit,
        "r2_fit": r2_fit,
        "pipeline": model
    }



In [2]:
# Analisis de las ventas

# 1. Preparación de tus datos
ventas_horizontal_df = pd.DataFrame({
    "Fecha": [
        "2021-12","2022-03","2022-08","2022-11",
        "2023-02","2023-05","2023-08","2023-11",
        "2024-02","2024-05","2024-08","2024-11",
        "2025-02","2025-05","2025-08","2025-11"
    ],
    "Absorción": [
        36.1, 21.3, 84, 64.8, 70.8, 91.5,
        42.5, 47.3, 43.3, 19, 28.9, 79.3,
        40.3, 36.7, 12.6, 25
    ],
    "precio_final_prom": [
        2812127, 2518970, 2394729, 2819731, 2705412, 3477620, 
        3602268, 3446037, 3521113, 3499479, 3606924, 3692115,
        3623229, 3650369, 3704248, 3705188
    ],
    "numero_proyectos_activos": [
        16, 17, 18, 19, 19, 23, 
        26, 26, 25, 21, 20, 20,
        23, 22, 21, 20
    ], 
    "Inventario_horizontal_disponible": [
        571, 908, 1274, 1078, 920, 905, 
        911, 895, 776, 818, 758, 822,
        830, 746, 757, 767
    ],
    

})

ventas_horizontal_df["Fecha"] = pd.to_datetime(ventas_horizontal_df["Fecha"])

# --------------------------------------------------------
if __name__ == "__main__":
    try:
        data_audit = EDA_master(ventas_horizontal_df)
        print("\n✅ EDA Finalizado con éxito. Diccionario de resultados generado.")
    except Exception as e:
        print(f"\n❌ Error en la ejecución: {e}")



--- INICIO DE AUDITORÍA DE DATOS ---
✅ Validación Estructural:
   - Fecha: Original
   - Ordenado: Sí (Se aplicó sort)
   - Duplicados eliminados: 0
   - Columna 'Absorción': Numérica ✓ | Valores nulos: 0
   - Columna 'precio_final_prom': Numérica ✓ | Valores nulos: 0
   - Columna 'numero_proyectos_activos': Numérica ✓ | Valores nulos: 0
   - Columna 'Inventario_horizontal_disponible': Numérica ✓ | Valores nulos: 0
------------------------------------------------------------

📊 ANALIZANDO SERIE: ABSORCIÓN
   🔹 Rango: Máximo de 91.50 (2023-05-01) | Mínimo de 12.60 (2025-08-01)
   🔹 Centralidad: Media 46.46 | Mediana 41.40 (Diferencia: 12.2%)
   🔹 Volatilidad: Desviación 24.51 (Dispersión alta, CV=52.8%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.2384 -> Normal (Gaussiana)


   🔹 Outliers detectados (Método IQR): 0


   🔹 Dinámica Reciente: Último cambio de +98.4% (Positivo)


   🔹 Memoria de la serie: Lags significativos en [] (Patrones repetitivos)

📊 ANALIZANDO SERIE: PRECIO_FINAL_PROM
   🔹 Rango: Máximo de 3,705,188.00 (2025-11-01) | Mínimo de 2,394,729.00 (2022-08-01)
   🔹 Centralidad: Media 3,298,722.44 | Mediana 3,510,296.00 (Diferencia: -6.0%)
   🔹 Volatilidad: Desviación 468,146.75 (Dispersión baja, CV=14.2%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0016 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 0


...

   🔹 Dinámica Reciente: Último cambio de -4.8% (Negativo)


   🔹 Memoria de la serie: Lags significativos en [1] (Patrones repetitivos)

📊 ANALIZANDO SERIE: INVENTARIO_HORIZONTAL_DISPONIBLE
   🔹 Rango: Máximo de 1,274.00 (2022-08-01) | Mínimo de 571.00 (2021-12-01)
   🔹 Centralidad: Media 858.50 | Mediana 826.00 (Diferencia: 3.9%)
   🔹 Volatilidad: Desviación 156.63 (Dispersión baja, CV=18.2%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0647 -> Normal (Gaussiana)


   🔹 Outliers detectados (Método IQR): 1
     Fechas clave: [datetime.date(2022, 8, 1)]


   🔹 Dinámica Reciente: Último cambio de +1.3% (Positivo)


   🔹 Memoria de la serie: Lags significativos en [] (Patrones repetitivos)

✅ EDA Finalizado con éxito. Diccionario de resultados generado.


# Creditos otorgados en Mazatlán

In [3]:
# Creditos hipotecarios en Mazatlán

import sys

# Directorio donde se encuentra la carpeta "Funciones"
sys.path.append(r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas")
from Funciones.Funciones import leer_archivo

# Token personal del INEGI
TOKEN = 'ccf9a2b3-64b9-4eb8-f202-a8cd92076d04'

'''
Se descargo la base de datos de la pagina https://sniiv.sedatu.gob.mx/Cubo/financiamiento#

Con los filtros del año 2022 al 2025
Estado: Sinaloa
Municipio: Mazatlán
Variables Modalidad, Tipo de crédito y mes 
En el eje y año y mes
En las columnas tipo de crédito: filtrado por 'Crédito individual'
En la segunda columna 'modalidad' solo vivienda existntes y viviendas nuevas
Se descargo el excel, se tranformo y limpio la base de datos para guardarla en la caprte BD_variables macro

'''


# Leer archivo
creditos_hipo_mazatlan_individual = leer_archivo(r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas\Proyectos\REM\BD variables macro\Creditos_hipotecarios_Mazatlán_Diciembre- 2025.csv", hoja=1)

creditos_hipo_mazatlan_individual["Fecha"] = pd.to_datetime(
    creditos_hipo_mazatlan_individual["Fecha"],
    format="%d/%m/%Y"
)
creditos_hipo_mazatlan_individual.rename(columns={"Viviendas nuevas": "Creditos_otrogados_viviendas_nuevas"}, inplace=True)
creditos_hipo_mazatlan_individual.rename(columns={"Viviendas existentes": "Creditos_otrogados_viviendas_existentes"}, inplace=True)
creditos_hipo_mazatlan_individual.drop(columns=["Total"], inplace=True)




# Analisis de las Creditos hipotecarios en Mazatlán
# --------------------------------------------------------
if __name__ == "__main__":

    try:
        data_audit_creditos = EDA_master(creditos_hipo_mazatlan_individual)
        print("\n✅ EDA Finalizado con éxito. Diccionario de resultados generado.")
    except Exception as e:
        print(f"\n❌ Error en la ejecución: {e}")

--- INICIO DE AUDITORÍA DE DATOS ---
✅ Validación Estructural:
   - Fecha: Original
   - Ordenado: Sí (Se aplicó sort)
   - Duplicados eliminados: 0
   - Columna 'Creditos_otrogados_viviendas_nuevas': Numérica ✓ | Valores nulos: 0
   - Columna 'Creditos_otrogados_viviendas_existentes': Numérica ✓ | Valores nulos: 0
------------------------------------------------------------

📊 ANALIZANDO SERIE: CREDITOS_OTROGADOS_VIVIENDAS_NUEVAS
   🔹 Rango: Máximo de 309.00 (2019-12-01) | Mínimo de 58.00 (2025-01-01)
   🔹 Centralidad: Media 162.65 | Mediana 170.00 (Diferencia: -4.3%)
   🔹 Volatilidad: Desviación 52.41 (Dispersión alta, CV=32.2%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.2961 -> Normal (Gaussiana)


   🔹 Outliers detectados (Método IQR): 1
     Fechas clave: [datetime.date(2019, 12, 1)]


   🔹 Dinámica Reciente: Último cambio de -6.8% (Negativo)


   🔹 Memoria de la serie: Lags significativos en [1, 2] (Patrones repetitivos)

📊 ANALIZANDO SERIE: CREDITOS_OTROGADOS_VIVIENDAS_EXISTENTES
   🔹 Rango: Máximo de 197.00 (2021-06-01) | Mínimo de 31.00 (2025-06-01)
   🔹 Centralidad: Media 110.79 | Mediana 116.50 (Diferencia: -4.9%)
   🔹 Volatilidad: Desviación 39.16 (Dispersión alta, CV=35.3%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0629 -> Normal (Gaussiana)


   🔹 Outliers detectados (Método IQR): 1
     Fechas clave: [datetime.date(2021, 6, 1)]


   🔹 Dinámica Reciente: Último cambio de -17.1% (Negativo)


   🔹 Memoria de la serie: Lags significativos en [1, 2, 3, 6, 12] (Patrones repetitivos)

✅ EDA Finalizado con éxito. Diccionario de resultados generado.


# Tasa de interes

In [4]:
# Tasa de interes de referencia
# ---- Extracción de la tasa objetivo diaria del Banco de México ---- #

import requests

token_banxico = '3f1b778eb9764c78aebf314182c78d98f26cc66dfae50d4a5fc61a61f52015f6'

# ID de la serie de tasa objetivo diaria
serie_id = 'SF61745' 

url = f'https://www.banxico.org.mx/SieAPIRest/service/v1/series/{serie_id}/datos'


headers = {'Bmx-Token': token_banxico}

response = requests.get(url, headers=headers)

if response.status_code == 200:
    datos = response.json()
    observaciones = datos['bmx']['series'][0]['datos']
    
    df_tasa = pd.DataFrame(observaciones)
    df_tasa['Fecha'] = pd.to_datetime(df_tasa['fecha'], dayfirst=True)
    df_tasa['Tasa objetivo diaria'] = pd.to_numeric(df_tasa['dato'], errors='coerce')
    df_tasa = df_tasa[['Fecha', 'Tasa objetivo diaria']].sort_values('Fecha')
    #display(df_tasa.tail())
else:
    print("Error en la consulta:", response.status_code)
    print(response.text[:500])


# Asegurarte de que la fecha sea el índice
df_tasa.set_index('Fecha', inplace=True)

# Calcular promedio de tasa por trimestre (fin de trimestre)
df_trimestral_raw = df_tasa.resample('MS').mean()

# Resetear índice si lo necesitas como columna
df_tasa_trimestral = df_trimestral_raw.reset_index()
df_tasa_trimestral.columns = ['Fecha', 'tasa_referencia']



# Analisis de la tasa de interes
# --------------------------------------------------------
if __name__ == "__main__":

    try:
        data_audit_tasa_interes = EDA_master(df_tasa_trimestral)
        print("\n✅ EDA Finalizado con éxito. Diccionario de resultados generado.")
    except Exception as e:
        print(f"\n❌ Error en la ejecución: {e}")

--- INICIO DE AUDITORÍA DE DATOS ---
✅ Validación Estructural:
   - Fecha: Original
   - Ordenado: Sí (Se aplicó sort)
   - Duplicados eliminados: 0
   - Columna 'tasa_referencia': Numérica ✓ | Valores nulos: 0
------------------------------------------------------------

📊 ANALIZANDO SERIE: TASA_REFERENCIA
   🔹 Rango: Máximo de 11.25 (2023-04-01) | Mínimo de 3.00 (2014-07-01)
   🔹 Centralidad: Media 6.19 | Mediana 5.32 (Diferencia: 16.4%)
   🔹 Volatilidad: Desviación 2.48 (Dispersión alta, CV=40.0%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0000 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 0


   🔹 Dinámica Reciente: Último cambio de -2.0% (Negativo)


   🔹 Memoria de la serie: Lags significativos en [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12] (Patrones repetitivos)

✅ EDA Finalizado con éxito. Diccionario de resultados generado.


# Personas Economicamente activas Sinaloa

In [5]:
# Personas económicamente activas y tasa de desempleo tasa de desempleo
# URL para obtener el personas economicamente activas (PEA) a nivel nacional
url_empleo = f' https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/6200093960/es/25/false/BISE/2.0/{TOKEN}?type=json'

response_empleo = requests.get(url_empleo)
data_empleo = response_empleo.json()

mes_inicio_trimestre = {
    '01': '01',  # Q1 → enero
    '02': '04',  # Q2 → abril
    '03': '07',  # Q3 → julio
    '04': '10'   # Q4 → octubre
}

# Extraer valores
valores_empleo = data_empleo['Series'][0]['OBSERVATIONS']
# Convertir a DataFrame
df_empleo = pd.DataFrame(valores_empleo)
# Separar año y trimestre
df_empleo[['anio', 'trimestre']] = df_empleo['TIME_PERIOD'].str.split('/', expand=True)
# Crear columna de fecha válida
df_empleo['Fecha'] = pd.to_datetime(df_empleo['anio'] + '-' + df_empleo['trimestre'].map(mes_inicio_trimestre) + '-01')
# Dar Formato de valores númericos
df_empleo['PEA'] = pd.to_numeric(df_empleo['OBS_VALUE'], errors='coerce')
# Ordenar las fechas de mas antiguo al más reciente
df_empleo = df_empleo[['Fecha', 'PEA']].sort_values('Fecha')

# URL para obtener el población desempleada a nivel nacional
url_desempleo = f'https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/6200093973/es/25/false/BISE/2.0/{TOKEN}?type=json'

response_desempleo = requests.get(url_desempleo)
data_desempleo = response_desempleo.json()

# Extraer valores
valores_desempleo = data_desempleo['Series'][0]['OBSERVATIONS']
# Convertir a DataFrame
df_desempleo = pd.DataFrame(valores_desempleo)
# Separar año y trimestre
df_desempleo[['anio', 'trimestre']] = df_desempleo['TIME_PERIOD'].str.split('/', expand=True)
# Crear columna de fecha válida
df_desempleo['Fecha'] = pd.to_datetime(df_desempleo['anio'] + '-' + df_desempleo['trimestre'].map(mes_inicio_trimestre) + '-01')
# Dar Formato de valores númericos
df_desempleo['valor'] = pd.to_numeric(df_desempleo['OBS_VALUE'], errors='coerce')
# Ordenar las fechas de mas antiguo al más reciente
df_desempleo = df_desempleo[['Fecha', 'valor']].sort_values('Fecha')

# Unir los DataFrames de empleo y desempleo
df_empleo['desempleo'] = df_desempleo['valor']

# Calcular la tasa de desempleo
df_empleo['tasa_desempleo'] = (df_empleo['desempleo'] / df_empleo['PEA']) * 100

df_empleo["Fecha"] = pd.to_datetime(df_empleo["Fecha"])
df_empleo = df_empleo.sort_values("Fecha").reset_index(drop=True)
df_empleo["Fecha"] = pd.to_datetime(
    df_empleo["Fecha"],
    format="%d/%m/%Y"
)

# Analisis de las empleo
# --------------------------------------------------------
if __name__ == "__main__":

    # Ejecutamos la función maestra
    try:
        data_audit_emploe = EDA_master(df_empleo)
        print("\n✅ EDA Finalizado con éxito. Diccionario de resultados generado.")
    except Exception as e:
        print(f"\n❌ Error en la ejecución: {e}")

--- INICIO DE AUDITORÍA DE DATOS ---
✅ Validación Estructural:
   - Fecha: Original
   - Ordenado: Sí (Se aplicó sort)
   - Duplicados eliminados: 0
   - Columna 'PEA': Numérica ✓ | Valores nulos: 1 | Fechas: ['2020-04-01']
   - Columna 'desempleo': Numérica ✓ | Valores nulos: 1 | Fechas: ['2020-04-01']
   - Columna 'tasa_desempleo': Numérica ✓ | Valores nulos: 1 | Fechas: ['2020-04-01']
------------------------------------------------------------

📊 ANALIZANDO SERIE: PEA
   🔹 Rango: Máximo de 1,505,813.00 (2024-04-01) | Mínimo de 1,112,471.00 (2005-07-01)
   🔹 Centralidad: Media 1,303,544.90 | Mediana 1,298,884.00 (Diferencia: 0.4%)
   🔹 Volatilidad: Desviación 108,555.06 (Dispersión baja, CV=8.3%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0122 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 0


   🔹 Dinámica Reciente: Último cambio de -1.7% (Negativo)


C:\Users\julio\AppData\Local\Temp\ipykernel_2508\666359320.py:180: FutureWarning:

The default fill_method='pad' in Series.pct_change is deprecated and will be removed in a future version. Either fill in any non-leading NA values prior to calling pct_change or specify 'fill_method=None' to not fill NA values.



   🔹 Memoria de la serie: Lags significativos en [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12] (Patrones repetitivos)

📊 ANALIZANDO SERIE: DESEMPLEO
   🔹 Rango: Máximo de 77,258.00 (2014-07-01) | Mínimo de 27,556.00 (2024-01-01)
   🔹 Centralidad: Media 46,829.78 | Mediana 45,681.50 (Diferencia: 2.5%)
   🔹 Volatilidad: Desviación 12,734.89 (Dispersión alta, CV=27.2%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0041 -> No Normal (Probable sesgo o outliers)


...

   🔹 Memoria de la serie: Lags significativos en [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12] (Patrones repetitivos)

📊 ANALIZANDO SERIE: TASA_DESEMPLEO
   🔹 Rango: Máximo de 6.15 (2011-07-01) | Mínimo de 1.86 (2024-01-01)
   🔹 Centralidad: Media 3.63 | Mediana 3.49 (Diferencia: 3.9%)
   🔹 Volatilidad: Desviación 1.08 (Dispersión alta, CV=29.8%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0020 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 0


   🔹 Dinámica Reciente: Último cambio de +17.3% (Positivo)


C:\Users\julio\AppData\Local\Temp\ipykernel_2508\666359320.py:180: FutureWarning:

The default fill_method='pad' in Series.pct_change is deprecated and will be removed in a future version. Either fill in any non-leading NA values prior to calling pct_change or specify 'fill_method=None' to not fill NA values.



   🔹 Memoria de la serie: Lags significativos en [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12] (Patrones repetitivos)

✅ EDA Finalizado con éxito. Diccionario de resultados generado.


# Indice Nacional de Precios al Consumidor INPC

In [6]:
# Índice Nacional de Precios al Consumidor (INPC)
# Indicador INPC general base 2018 = 100

# Construir URL para el INPC
url = f'https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/910399/es/00/false/BIE-BISE/2.0/{TOKEN}?type=json'

# Hacer la solicitud
response = requests.get(url)
data = response.json()

# Extraer observaciones
valores = data['Series'][0]['OBSERVATIONS']
df_inpc = pd.DataFrame(valores)

# Separar año y mes
df_inpc[['anio', 'mes']] = df_inpc['TIME_PERIOD'].str.split('/', expand=True)

# Crear columna de fecha
df_inpc['Fecha'] = pd.to_datetime(df_inpc['anio'] + '-' + df_inpc['mes'] + '-01')

# Convertir valores a numérico
df_inpc['INPC'] = pd.to_numeric(df_inpc['OBS_VALUE'], errors='coerce')

# Limpiar columnas y ordenar
df_inpc = df_inpc[['Fecha', 'INPC']].sort_values('Fecha')


df_inpc["Fecha"] = pd.to_datetime(df_inpc["Fecha"])
df_inpc = df_inpc.sort_values("Fecha").reset_index(drop=True)
df_inpc["Fecha"] = pd.to_datetime(
    df_inpc["Fecha"],
    format="%d/%m/%Y"
)
df_inpc = df_inpc[df_inpc['Fecha']>= '2018-01-01'].copy()

# Analisis de las inpc
# --------------------------------------------------------
if __name__ == "__main__":
    try:
        data_audi_inpc = EDA_master(df_inpc)
        print("\n✅ EDA Finalizado con éxito. Diccionario de resultados generado.")
    except Exception as e:
        print(f"\n❌ Error en la ejecución: {e}")



--- INICIO DE AUDITORÍA DE DATOS ---
✅ Validación Estructural:
   - Fecha: Original
   - Ordenado: Sí (Se aplicó sort)
   - Duplicados eliminados: 0
   - Columna 'INPC': Numérica ✓ | Valores nulos: 0
------------------------------------------------------------

📊 ANALIZANDO SERIE: INPC
   🔹 Rango: Máximo de 1.14 (2021-11-01) | Mínimo de -1.01 (2020-04-01)
   🔹 Centralidad: Media 0.39 | Mediana 0.39 (Diferencia: 0.9%)
   🔹 Volatilidad: Desviación 0.33 (Dispersión alta, CV=84.3%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0060 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 3
     Fechas clave: [datetime.date(2018, 4, 1), datetime.date(2020, 4, 1), datetime.date(2021, 11, 1)]


   🔹 Dinámica Reciente: Último cambio de +83.3% (Positivo)


   🔹 Memoria de la serie: Lags significativos en [1, 12] (Patrones repetitivos)

✅ EDA Finalizado con éxito. Diccionario de resultados generado.


# Pasajeros OMA 

In [7]:
# Pasajeron aéreos de OMA Mazatlán 
# https://www.oma.aero/es/nuestros-servicios/aviacion-comercial/mazatlan-c/estadisticas-de-pasajeros.php

import warnings
warnings.filterwarnings('ignore', category=FutureWarning)

MESES_MAP = {
    "Enero": 1, "January": 1,
    "Febrero": 2, "February": 2,
    "Marzo": 3, "March": 3,
    "Abril": 4, "April": 4,
    "Mayo": 5, "May": 5,
    "Junio": 6, "June": 6,
    "Julio": 7, "July": 7,
    "Agosto": 8, "August": 8,
    "Septiembre": 9, "September": 9,
    "Octubre": 10, "October": 10,
    "Noviembre": 11, "November": 11,
    "Diciembre": 12, "December": 12,
}

def limpiar_tabla(df, tipo):
    df = df.copy()

    # --- 1. Quitar filas Annual Total ---
    df = df[~df.iloc[:,0].astype(str).str.contains("Annual", case=False)]

    # --- 2. Detectar filas que contienen solo el año ---
    df["EsAño"] = df.iloc[:,0].astype(str).str.fullmatch(r"\d{4}")

    # Crear columna Año propagando hacia abajo
    df["Año"] = df.loc[df["EsAño"], df.columns[0]]
    df["Año"] = df["Año"].ffill()
    # Luego convertimos a int cuando ya no hay NaN
    df["Año"] = pd.to_numeric(df["Año"], errors='coerce')

    # --- 3. Quitar filas que solo tienen el año ---
    df = df[~df["EsAño"]]

    # --- 4. Extraer el mes del texto "Enero / January" ---
    df["MesTexto"] = df.iloc[:,0].str.split("/").str[0].str.strip()
    df["Mes"] = df["MesTexto"].map(MESES_MAP)

    # --- 5. Crear columna Fecha ---
    df["Fecha"] = pd.to_datetime(dict(year=df["Año"].astype(int), month=df["Mes"], day=1))

    # --- 6. Borrar columnas basura ---
    df = df.drop(columns=["EsAño", "MesTexto", "Mes"])

    # --- 7. Pasar a LONG FORMAT ---
    df_long = df.melt(
        id_vars=["Fecha"],
        value_vars=df.columns[1:-1],  # todas menos la columna original del mes y Año
        var_name="Aeropuerto",
        value_name="Pasajeros"
    )

    df_long["Tipo"] = tipo

    return df_long


URL_OMA = "https://www.oma.aero/assets/002/5843.xlsx"
SHEET = 0  # o el nombre de la hoja si lo conoces

def cargar_tablas_oma(url=URL_OMA, sheet_name=SHEET):
    # Leemos toda la hoja sin encabezados para poder cortar por posición
    raw = pd.read_excel(url, sheet_name=sheet_name, header=None)

    # Filas 4 a 368  -> en iloc son 3:368  (fin excluyente)
    fila_ini = 3
    fila_fin = 368

    # Tabla 1: A4:O368  -> columnas A(0) a O(14) => 0:15
    dom = raw.iloc[fila_ini:fila_fin, 0:15].copy()

    # Tabla 2: Q4:AE368 -> Q(16) a AE(30) => 16:31
    intl = raw.iloc[fila_ini:fila_fin, 16:31].copy()

    

    # La primera fila de cada rango es el encabezado
    for df in (dom, intl):
        df.columns = df.iloc[0]          # fila de encabezados
        df.drop(df.index[0], inplace=True)
        df.reset_index(drop=True, inplace=True)

    return dom, intl

dom, intl = cargar_tablas_oma()

# La columna Año /YEAR está en ambas tablas, la copiamos a intl porque en la original estaba mal
intl['AÑO /YEAR'] = dom['AÑO /YEAR']

dom_clean  = limpiar_tabla(dom,  "Pasajeros_Nacionales")
intl_clean = limpiar_tabla(intl, "Pasajeros_Internacionales")


# Tabla final unificada
oma = pd.concat([dom_clean, intl_clean], ignore_index=True)

# Pivotear
oma = oma.pivot_table(
    index=["Fecha", "Aeropuerto"],
    columns="Tipo",
    values="Pasajeros",
    aggfunc="sum"
).reset_index()

# Limpieza de datos
oma = oma[(oma['Aeropuerto'] != 'Año') & (oma['Aeropuerto'] != 'Total')]
oma = oma[oma["Aeropuerto"]=="MZT"]

oma["Fecha"] = pd.to_datetime(oma["Fecha"])
oma = oma.sort_values("Fecha").reset_index(drop=True)
oma["Fecha"] = pd.to_datetime(
    oma["Fecha"],
    format="%d/%m/%Y"
)

oma = oma[[ "Fecha", "Pasajeros_Nacionales", "Pasajeros_Internacionales"]]

columnas = ["Pasajeros_Nacionales", "Pasajeros_Internacionales"]   

oma[columnas] = oma[columnas].apply(pd.to_numeric, errors='coerce')


# Analisis de las oma
# --------------------------------------------------------
if __name__ == "__main__":
    try:
        data_audi_inpc = EDA_master(oma)
        print("\n✅ EDA Finalizado con éxito. Diccionario de resultados generado.")
    except Exception as e:
        print(f"\n❌ Error en la ejecución: {e}")


--- INICIO DE AUDITORÍA DE DATOS ---
✅ Validación Estructural:
   - Fecha: Original
   - Ordenado: Sí (Se aplicó sort)
   - Duplicados eliminados: 0
   - Columna 'Pasajeros_Nacionales': Numérica ✓ | Valores nulos: 0
   - Columna 'Pasajeros_Internacionales': Numérica ✓ | Valores nulos: 0
------------------------------------------------------------

📊 ANALIZANDO SERIE: PASAJEROS_NACIONALES
   🔹 Rango: Máximo de 151,257.00 (2024-07-01) | Mínimo de 0.00 (2025-12-01)
   🔹 Centralidad: Media 53,172.35 | Mediana 42,498.50 (Diferencia: 25.1%)
   🔹 Volatilidad: Desviación 29,257.64 (Dispersión alta, CV=55.0%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0000 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 19
     Fechas clave: [datetime.date(2023, 6, 1), datetime.date(2023, 7, 1), datetime.date(2023, 8, 1), datetime.date(2023, 12, 1), datetime.date(2024, 3, 1), datetime.date(2024, 4, 1), datetime.date(2024, 5, 1), datetime.date(2024, 6, 1), datetime.date(2024, 7, 1), datetime.date(2024, 8, 1), datetime.date(2024, 9, 1), datetime.date(2024, 10, 1), datetime.date(2024, 12, 1), datetime.date(2025, 3, 1), datetime.date(2025, 4, 1), datetime.date(2025, 5, 1), datetime.date(2025, 6, 1), datetime.date(2025, 7, 1), datetime.date(2025, 8, 1)]


   🔹 Dinámica Reciente: Último cambio de -100.0% (Negativo)


   🔹 Memoria de la serie: Lags significativos en [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12] (Patrones repetitivos)

📊 ANALIZANDO SERIE: PASAJEROS_INTERNACIONALES
   🔹 Rango: Máximo de 75,126.00 (2001-03-01) | Mínimo de 0.00 (2025-12-01)
   🔹 Centralidad: Media 26,950.97 | Mediana 24,752.50 (Diferencia: 8.9%)
   🔹 Volatilidad: Desviación 14,964.71 (Dispersión alta, CV=55.5%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0000 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 1
     Fechas clave: [datetime.date(2001, 3, 1)]


   🔹 Dinámica Reciente: Último cambio de -100.0% (Negativo)


   🔹 Memoria de la serie: Lags significativos en [1, 2, 3, 4, 5, 6, 7, 8, 10, 11, 12] (Patrones repetitivos)

✅ EDA Finalizado con éxito. Diccionario de resultados generado.


# Número de turistas

In [8]:
# Número de turistas
turistas_datatur = leer_archivo(r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas\Proyectos\REM\BD variables macro\Turistas-Mazatlan-DataTur.csv", hoja=1)

turistas_datatur["Fecha"] = pd.to_datetime(
    turistas_datatur["Fecha"],
    format="%d/%m/%Y"
)


turistas_datatur = turistas_datatur[turistas_datatur['Fecha'] <= '2025-08-01'].copy()
turistas_datatur = turistas_datatur.drop(columns=['Pasajeros_1_estrellas'])


# Analisis de Número de turistas
# --------------------------------------------------------
if __name__ == "__main__":
    try:
        data_audi_inpc = EDA_master(turistas_datatur)
        print("\n✅ EDA Finalizado con éxito. Diccionario de resultados generado.")
    except Exception as e:
        print(f"\n❌ Error en la ejecución: {e}")



--- INICIO DE AUDITORÍA DE DATOS ---
✅ Validación Estructural:
   - Fecha: Original
   - Ordenado: Sí (Se aplicó sort)
   - Duplicados eliminados: 0
   - Columna 'Pasajeros_5_estrellas': Numérica ✓ | Valores nulos: 0
   - Columna 'Pasajeros_4_estrellas': Numérica ✓ | Valores nulos: 0
   - Columna 'Pasajeros_3_estrellas': Numérica ✓ | Valores nulos: 0
   - Columna 'Pasajeros_2_estrellas': Numérica ✓ | Valores nulos: 0
------------------------------------------------------------

📊 ANALIZANDO SERIE: PASAJEROS_5_ESTRELLAS
   🔹 Rango: Máximo de 176,867.00 (2017-07-01) | Mínimo de 0.00 (2020-05-01)
   🔹 Centralidad: Media 93,618.37 | Mediana 94,719.00 (Diferencia: -1.2%)
   🔹 Volatilidad: Desviación 27,118.37 (Dispersión alta, CV=29.0%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0007 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 5
     Fechas clave: [datetime.date(2017, 6, 1), datetime.date(2017, 7, 1), datetime.date(2020, 4, 1), datetime.date(2020, 5, 1), datetime.date(2020, 6, 1)]


   🔹 Dinámica Reciente: Último cambio de -36.9% (Negativo)


   🔹 Memoria de la serie: Lags significativos en [1, 2, 3, 4, 8, 12] (Patrones repetitivos)

📊 ANALIZANDO SERIE: PASAJEROS_4_ESTRELLAS
   🔹 Rango: Máximo de 164,033.00 (2025-08-01) | Mínimo de 0.00 (2020-05-01)
   🔹 Centralidad: Media 59,848.46 | Mediana 59,497.50 (Diferencia: 0.6%)
   🔹 Volatilidad: Desviación 23,749.99 (Dispersión alta, CV=39.7%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0132 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 1
     Fechas clave: [datetime.date(2025, 8, 1)]


...

   🔹 Dinámica Reciente: Último cambio de +26.1% (Positivo)


   🔹 Memoria de la serie: Lags significativos en [1, 2, 3, 8, 11, 12] (Patrones repetitivos)

📊 ANALIZANDO SERIE: PASAJEROS_2_ESTRELLAS
   🔹 Rango: Máximo de 26,994.00 (2018-07-01) | Mínimo de 0.00 (2020-04-01)
   🔹 Centralidad: Media 8,909.62 | Mediana 8,609.00 (Diferencia: 3.5%)
   🔹 Volatilidad: Desviación 4,457.67 (Dispersión alta, CV=50.0%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0000 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 9
     Fechas clave: [datetime.date(2016, 7, 1), datetime.date(2017, 4, 1), datetime.date(2017, 7, 1), datetime.date(2017, 8, 1), datetime.date(2018, 7, 1), datetime.date(2018, 8, 1), datetime.date(2019, 7, 1), datetime.date(2019, 8, 1), datetime.date(2022, 7, 1)]


   🔹 Dinámica Reciente: Último cambio de +50.0% (Positivo)


   🔹 Memoria de la serie: Lags significativos en [1, 2, 3, 4, 5, 7, 8, 9, 11, 12] (Patrones repetitivos)

✅ EDA Finalizado con éxito. Diccionario de resultados generado.


# % de ocupación hetelera

In [9]:
# % de ocupación hetelera
porcentaje_ocu_hotelera = leer_archivo(r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas\Proyectos\REM\BD variables macro\Porcentaje_ocupación_hotelera_DataTur.csv", hoja=1)

porcentaje_ocu_hotelera["Fecha"] = pd.to_datetime(
    porcentaje_ocu_hotelera["Fecha"],
    format="%d/%m/%Y"
)


porcentaje_ocu_hotelera = porcentaje_ocu_hotelera[porcentaje_ocu_hotelera['Fecha'] <= '2025-08-01'].copy()


# Analisis de % de ocupación hetelera
# --------------------------------------------------------
if __name__ == "__main__":
    try:
        data_audi_inpc = EDA_master(porcentaje_ocu_hotelera)
        print("\n✅ EDA Finalizado con éxito. Diccionario de resultados generado.")
    except Exception as e:
        print(f"\n❌ Error en la ejecución: {e}")



--- INICIO DE AUDITORÍA DE DATOS ---
✅ Validación Estructural:
   - Fecha: Original
   - Ordenado: Sí (Se aplicó sort)
   - Duplicados eliminados: 0
   - Columna '%_ocupacion_5_estrellas': Numérica ✓ | Valores nulos: 0
   - Columna '%_ocupacion_4_estrellas': Numérica ✓ | Valores nulos: 0
   - Columna '%_ocupacion_3_estrellas': Numérica ✓ | Valores nulos: 0
   - Columna '%_ocupacion_2_estrellas': Numérica ✓ | Valores nulos: 0
------------------------------------------------------------

📊 ANALIZANDO SERIE: %_OCUPACION_5_ESTRELLAS
   🔹 Rango: Máximo de 92.10 (2019-07-01) | Mínimo de 0.00 (2020-05-01)
   🔹 Centralidad: Media 69.95 | Mediana 71.93 (Diferencia: -2.7%)
   🔹 Volatilidad: Desviación 14.27 (Dispersión alta, CV=20.4%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0000 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 5
     Fechas clave: [datetime.date(2020, 4, 1), datetime.date(2020, 5, 1), datetime.date(2020, 6, 1), datetime.date(2020, 7, 1), datetime.date(2021, 1, 1)]


   🔹 Dinámica Reciente: Último cambio de +4.5% (Positivo)


   🔹 Memoria de la serie: Lags significativos en [1, 2, 3, 4, 8] (Patrones repetitivos)

📊 ANALIZANDO SERIE: %_OCUPACION_4_ESTRELLAS
   🔹 Rango: Máximo de 84.38 (2022-07-01) | Mínimo de 0.00 (2020-05-01)
   🔹 Centralidad: Media 56.30 | Mediana 55.77 (Diferencia: 1.0%)
   🔹 Volatilidad: Desviación 15.20 (Dispersión alta, CV=27.0%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0000 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 3
     Fechas clave: [datetime.date(2020, 4, 1), datetime.date(2020, 5, 1), datetime.date(2020, 6, 1)]


...

   🔹 Dinámica Reciente: Último cambio de -10.2% (Negativo)


   🔹 Memoria de la serie: Lags significativos en [1, 2, 12] (Patrones repetitivos)

📊 ANALIZANDO SERIE: %_OCUPACION_2_ESTRELLAS
   🔹 Rango: Máximo de 57.68 (2019-07-01) | Mínimo de 0.00 (2020-04-01)
   🔹 Centralidad: Media 30.05 | Mediana 30.92 (Diferencia: -2.8%)
   🔹 Volatilidad: Desviación 10.58 (Dispersión alta, CV=35.2%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0051 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 9
     Fechas clave: [datetime.date(2014, 10, 1), datetime.date(2017, 7, 1), datetime.date(2018, 7, 1), datetime.date(2019, 6, 1), datetime.date(2019, 7, 1), datetime.date(2020, 4, 1), datetime.date(2020, 5, 1), datetime.date(2020, 6, 1), datetime.date(2024, 10, 1)]


   🔹 Dinámica Reciente: Último cambio de -6.8% (Negativo)


   🔹 Memoria de la serie: Lags significativos en [1, 2, 3, 4, 5, 7, 8, 12] (Patrones repetitivos)

✅ EDA Finalizado con éxito. Diccionario de resultados generado.


# Estadia promedio en hoteles

In [10]:
# Estadia promedio en hoteles
estadia_promedio = leer_archivo(r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas\Proyectos\REM\BD variables macro\Estadia_promedio_DataTur.csv", hoja=1)

estadia_promedio["Fecha"] = pd.to_datetime(
    estadia_promedio["Fecha"],
    format="%d/%m/%Y"
)


estadia_promedio = estadia_promedio[estadia_promedio['Fecha'] <= '2025-08-01'].copy()
estadia_promedio = estadia_promedio.drop(columns=['Estadia_promedio_1_estrellas'])



# Analisis de Estadia promedio en hoteles
# --------------------------------------------------------
if __name__ == "__main__":
    try:
        data_audi_inpc = EDA_master(estadia_promedio)
        print("\n✅ EDA Finalizado con éxito. Diccionario de resultados generado.")
    except Exception as e:
        print(f"\n❌ Error en la ejecución: {e}")


--- INICIO DE AUDITORÍA DE DATOS ---
✅ Validación Estructural:
   - Fecha: Original
   - Ordenado: Sí (Se aplicó sort)
   - Duplicados eliminados: 0
   - Columna 'Estadia_promedio_5_estrellas': Numérica ✓ | Valores nulos: 0
   - Columna 'Estadia_promedio_4_estrellas': Numérica ✓ | Valores nulos: 0
   - Columna 'Estadia_promedio_3_estrellas': Numérica ✓ | Valores nulos: 0
   - Columna 'Estadia_promedio_2_estrellas': Numérica ✓ | Valores nulos: 0
------------------------------------------------------------

📊 ANALIZANDO SERIE: ESTADIA_PROMEDIO_5_ESTRELLAS
   🔹 Rango: Máximo de 4.80 (2016-02-01) | Mínimo de 0.00 (2020-05-01)
   🔹 Centralidad: Media 2.99 | Mediana 2.93 (Diferencia: 1.9%)
   🔹 Volatilidad: Desviación 0.58 (Dispersión baja, CV=19.3%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0000 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 13
     Fechas clave: [datetime.date(2016, 1, 1), datetime.date(2016, 2, 1), datetime.date(2016, 3, 1), datetime.date(2016, 4, 1), datetime.date(2016, 7, 1), datetime.date(2016, 8, 1), datetime.date(2016, 11, 1), datetime.date(2016, 12, 1), datetime.date(2020, 4, 1), datetime.date(2020, 5, 1), datetime.date(2020, 6, 1), datetime.date(2022, 6, 1), datetime.date(2025, 8, 1)]


   🔹 Dinámica Reciente: Último cambio de +48.5% (Positivo)


   🔹 Memoria de la serie: Lags significativos en [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11] (Patrones repetitivos)

📊 ANALIZANDO SERIE: ESTADIA_PROMEDIO_4_ESTRELLAS
   🔹 Rango: Máximo de 2.81 (2025-01-01) | Mínimo de 0.00 (2020-05-01)
   🔹 Centralidad: Media 2.12 | Mediana 2.12 (Diferencia: -0.4%)
   🔹 Volatilidad: Desviación 0.28 (Dispersión baja, CV=13.3%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0000 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 6
     Fechas clave: [datetime.date(2020, 5, 1), datetime.date(2020, 6, 1), datetime.date(2022, 12, 1), datetime.date(2025, 1, 1), datetime.date(2025, 2, 1), datetime.date(2025, 7, 1)]


...

   🔹 Dinámica Reciente: Último cambio de +7.8% (Positivo)


   🔹 Memoria de la serie: Lags significativos en [1] (Patrones repetitivos)

📊 ANALIZANDO SERIE: ESTADIA_PROMEDIO_2_ESTRELLAS
   🔹 Rango: Máximo de 1.73 (2021-09-01) | Mínimo de 0.00 (2020-04-01)
   🔹 Centralidad: Media 1.40 | Mediana 1.44 (Diferencia: -2.2%)
   🔹 Volatilidad: Desviación 0.26 (Dispersión baja, CV=18.7%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0000 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 3
     Fechas clave: [datetime.date(2020, 4, 1), datetime.date(2020, 5, 1), datetime.date(2020, 6, 1)]


   🔹 Dinámica Reciente: Último cambio de +1.5% (Positivo)


   🔹 Memoria de la serie: Lags significativos en [1, 2] (Patrones repetitivos)

✅ EDA Finalizado con éxito. Diccionario de resultados generado.


# Densidad promedio hoteles

In [11]:
# Densidad promedio hoteles
densidad_promedio = leer_archivo(r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas\Proyectos\REM\BD variables macro\Densidad_habitacional_DataTur.csv", hoja=1)

densidad_promedio["Fecha"] = pd.to_datetime(
    densidad_promedio["Fecha"],
    format="%d/%m/%Y"
)


densidad_promedio = densidad_promedio[densidad_promedio['Fecha'] <= '2025-08-01'].copy()
densidad_promedio = densidad_promedio.drop(columns=['Densidad_prom_1_estrella'])

# Analisis de Densidad promedio hoteles
# --------------------------------------------------------
if __name__ == "__main__":
    try:
        data_audi_inpc = EDA_master(densidad_promedio)
        print("\n✅ EDA Finalizado con éxito. Diccionario de resultados generado.")
    except Exception as e:
        print(f"\n❌ Error en la ejecución: {e}")



--- INICIO DE AUDITORÍA DE DATOS ---
✅ Validación Estructural:
   - Fecha: Original
   - Ordenado: Sí (Se aplicó sort)
   - Duplicados eliminados: 0
   - Columna 'Densidad_prom_5_estrellas': Numérica ✓ | Valores nulos: 0
   - Columna 'Densidad_prom_4_estrellas': Numérica ✓ | Valores nulos: 0
   - Columna 'Densidad_prom_3_estrellas': Numérica ✓ | Valores nulos: 0
   - Columna 'Densidad_prom_2_estrellas': Numérica ✓ | Valores nulos: 0
------------------------------------------------------------

📊 ANALIZANDO SERIE: DENSIDAD_PROM_5_ESTRELLAS
   🔹 Rango: Máximo de 3.99 (2020-07-01) | Mínimo de 0.00 (2020-05-01)
   🔹 Centralidad: Media 3.22 | Mediana 3.29 (Diferencia: -2.4%)
   🔹 Volatilidad: Desviación 0.49 (Dispersión baja, CV=15.4%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0000 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 1
     Fechas clave: [datetime.date(2020, 5, 1)]


   🔹 Dinámica Reciente: Último cambio de +15.2% (Positivo)


   🔹 Memoria de la serie: Lags significativos en [1, 2, 3, 4] (Patrones repetitivos)

📊 ANALIZANDO SERIE: DENSIDAD_PROM_4_ESTRELLAS
   🔹 Rango: Máximo de 3.39 (2019-09-01) | Mínimo de 0.00 (2020-05-01)
   🔹 Centralidad: Media 2.55 | Mediana 2.54 (Diferencia: 0.2%)
   🔹 Volatilidad: Desviación 0.33 (Dispersión baja, CV=13.0%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0000 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 13
     Fechas clave: [datetime.date(2019, 7, 1), datetime.date(2019, 8, 1), datetime.date(2019, 9, 1), datetime.date(2020, 2, 1), datetime.date(2020, 3, 1), datetime.date(2020, 4, 1), datetime.date(2020, 5, 1), datetime.date(2020, 6, 1), datetime.date(2020, 8, 1), datetime.date(2021, 5, 1), datetime.date(2021, 6, 1), datetime.date(2025, 1, 1), datetime.date(2025, 2, 1)]


...

   🔹 Dinámica Reciente: Último cambio de -0.4% (Negativo)


   🔹 Memoria de la serie: Lags significativos en [1] (Patrones repetitivos)

📊 ANALIZANDO SERIE: DENSIDAD_PROM_2_ESTRELLAS
   🔹 Rango: Máximo de 2.77 (2018-07-01) | Mínimo de 0.00 (2020-04-01)
   🔹 Centralidad: Media 2.00 | Mediana 2.05 (Diferencia: -2.4%)
   🔹 Volatilidad: Desviación 0.42 (Dispersión alta, CV=20.9%)
   🔹 Prueba de Normalidad (Shapiro-Wilk): p-value=0.0000 -> No Normal (Probable sesgo o outliers)


   🔹 Outliers detectados (Método IQR): 5
     Fechas clave: [datetime.date(2018, 7, 1), datetime.date(2018, 8, 1), datetime.date(2020, 4, 1), datetime.date(2020, 5, 1), datetime.date(2020, 6, 1)]


   🔹 Dinámica Reciente: Último cambio de +6.1% (Positivo)


   🔹 Memoria de la serie: Lags significativos en [1, 2] (Patrones repetitivos)

✅ EDA Finalizado con éxito. Diccionario de resultados generado.


# Merge de las variables

In [12]:
# ============================================================
# Hacer el merge por Fecha con creditos_hipo_mazatlan_individual
# ============================================================
df_ventas = ventas_horizontal_df.merge(
    creditos_hipo_mazatlan_individual,
    on="Fecha",
    how="left"
)

# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
df_ventas = df_ventas.merge(
    df_tasa_trimestral,
    on="Fecha",
    how="left"
)

# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
cols_macro = ["Fecha", "PEA", "desempleo", "tasa_desempleo"]

df_ventas = pd.merge_asof(
    df_ventas,
    df_empleo[cols_macro],
    on="Fecha",          # columna común
    direction="backward" # usa el último dato <= Fecha de ventas
)


# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
df_ventas = df_ventas.merge(
    df_inpc,
    on="Fecha",
    how="left"
)

# ============================================================
# Hacer el merge por Fecha con pasajeros de OMA
# ============================================================
df_ventas = df_ventas.merge(
    oma,
    on="Fecha",
    how="left"
)

# ============================================================
# Hacer el merge por Fecha con turistas_datatur
# ============================================================
df_ventas = df_ventas.merge(
    turistas_datatur,
    on="Fecha",
    how="left"
)

# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
df_ventas = df_ventas.merge(
    porcentaje_ocu_hotelera,
    on="Fecha",
    how="left"
)


# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
df_ventas = df_ventas.merge(
    estadia_promedio,
    on="Fecha",
    how="left"
)

# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
df_ventas = df_ventas.merge(
    densidad_promedio,
    on="Fecha",
    how="left"
)
df_ventas

Fecha  Absorción  precio_final_prom  numero_proyectos_activos  \
0  2021-12-01       36.1            2812127                        16   
1  2022-03-01       21.3            2518970                        17   
2  2022-08-01       84.0            2394729                        18   
3  2022-11-01       64.8            2819731                        19   
4  2023-02-01       70.8            2705412                        19   
5  2023-05-01       91.5            3477620                        23   
6  2023-08-01       42.5            3602268                        26   
7  2023-11-01       47.3            3446037                        26   
8  2024-02-01       43.3            3521113                        25   
9  2024-05-01       19.0            3499479                        21   
10 2024-08-01       28.9            3606924                        20   
11 2024-11-01       79.3            3692115                        20   
12 2025-02-01       40.3            3623229                        23   
13 2025-05-01       36.7            3650369                        22   
14 2025-08-01       12.6            3704248                        21   
15 2025-11-01       25.0            3705188                        20   

    Inventario_horizontal_disponible  Creditos_otrogados_viviendas_nuevas  \
0                                571                                238.0   
1                                908                                170.0   
2                               1274                                188.0   
3                               1078                                196.0   
4                                920                                110.0   
5                                905                                202.0   
6                                911                                224.0   
7                                895                                170.0   
8                                776                                140.0   
9                                818                                144.0   
10                               758                                169.0   
11                               822                                178.0   
12                               830                                 64.0   
13                               746                                 80.0   
14                               757                                 68.0   
15                               767                                  NaN   

    Creditos_otrogados_viviendas_existentes  tasa_referencia        PEA  \
0                                     163.0         5.241935  1380214.0   
1                                      97.0         6.112903  1373253.0   
2                                      94.0         8.233871  1414126.0   
3                                     104.0         9.750000  1466293.0   
4                                      96.0        10.839286  1484243.0   
5                                      92.0        11.250000  1472153.0   
6                                     128.0        11.250000  1493727.0   
7                                     104.0        11.250000  1499528.0   
8                                     118.0        11.250000  1481795.0   
9                                     126.0        11.000000  1505813.0   
10                                    105.0        10.816667  1452621.0   
11                                    128.0        10.362069  1479725.0   
12                                     38.0         9.607143  1481009.0   
13                                     43.0         8.741935  1481895.0   
14                                     34.0         7.806452  1456940.0   
15                                      NaN         7.300000  1456940.0   

    desempleo  ...  %_ocupacion_3_estrellas  %_ocupacion_2_estrellas  \
0     37831.0  ...                    64.03                    33.65   
1     36521.0  ...                  

In [13]:
# 5.1 Gráfico interactivo doble eje
fig = plot_absorcion_vs_variable(df_ventas, target="Absorción", default_var="precio_final_prom")
fig.show()

In [14]:
# Analisis correlaciones 
# ============================================================
analisis_estadistico(df_ventas, target="Absorción")



REPORTE EDA MULTIVARIABLE (con interpretación automática)
Registros: 16 | Variables numéricas: 29
Rango fechas: 2021-12-01 a 2025-11-01
-----------------------------------------------------------------------------------------------

A) CORRELACIONES VS TARGET (Pearson / Spearman / Kendall)


Pearson  Spearman  Kendall  |Pearson|
Absorción                                  1.000     1.000    1.000      1.000
Estadia_promedio_5_estrellas              -0.665    -0.692   -0.478      0.665
Inventario_horizontal_disponible           0.580     0.606    0.433      0.580
Estadia_promedio_3_estrellas              -0.509    -0.418   -0.320      0.509
Densidad_prom_5_estrellas                 -0.454    -0.481   -0.325      0.454
Pasajeros_Nacionales                      -0.440    -0.391   -0.267      0.440
tasa_referencia                            0.362     0.447    0.308      0.362
Pasajeros_4_estrellas                     -0.357    -0.300   -0.238      0.357
Creditos_otrogados_viviendas_nuevas        0.350     0.388    0.287      0.350
Densidad_prom_3_estrellas                 -0.331    -0.392   -0.248      0.331
precio_final_prom                         -0.303    -0.356   -0.300      0.303
Pasajeros_5_estrellas                      0.294     0.086    0.067      0.294
Pasajeros_3_estrellas                     -0.288    -0.386   -0.352      0.288
Densidad_prom_4_estrellas                 -0.262    -0.362   -0.232      0.262
%_ocupacion_2_estrellas                    0.167     0.204    0.181      0.167
%_ocupacion_3_estrellas                    0.165     0.375    0.257      0.165
Creditos_otrogados_viviendas_existentes    0.160    -0.014   -0.067      0.160
%_ocupacion_5_estrellas                   -0.159    -0.171   -0.143      0.159
PEA                                        0.118     0.163    0.092      0.118
Densidad_prom_2_estrellas                 -0.114    -0.238   -0.202      0.114
tasa_desempleo                            -0.097    -0.140   -0.025      0.097
desempleo                                 -0.089    -0.181   -0.059      0.089
INPC                                       0.071     0.157    0.126      0.071
Estadia_promedio_4_estrellas              -0.069     0.166    0.134      0.069
Pasajeros_Internacionales                  0.061     0.176    0.117      0.061
%_ocupacion_4_estrellas                   -0.060    -0.064   -0.048      0.060
Estadia_promedio_2_estrellas              -0.037    -0.020   -0.048      0.037
Pasajeros_2_estrellas                     -0.031    -0.204   -0.143      0.031
numero_proyectos_activos                   0.000     0.089    0.077      0.000


A.1) Interpretación automática (por variable vs target)

• Estadia_promedio_5_estrellas
  - Pearson  = -0.665 → Moderada negativa: impacto importante (p.ej. sobreoferta/costo).
  - Spearman = -0.692 → Moderada negativa: impacto importante (p.ej. sobreoferta/costo).
  - Kendall  = -0.478 → Débil negativa: fricción ligera sobre el target.
  - Forma    → Relación aproximadamente lineal (Pearson ≈ Spearman/Kendall).

• Inventario_horizontal_disponible
  - Pearson  =  0.580 → Moderada positiva: relación relevante. Investigar causalidad/segmentación.
  - Spearman =  0.606 → Moderada positiva: relación relevante. Investigar causalidad/segmentación.
  - Kendall  =  0.433 → Débil positiva: señal marginal. No es driver principal.
  - Forma    → Relación aproximadamente lineal (Pearson ≈ Spearman/Kendall).

• Estadia_promedio_3_estrellas
  - Pearson  = -0.509 → Moderada negativa: impacto importante (p.ej. sobreoferta/costo).
  - Spearman = -0.418 → Débil negativa: fricción ligera sobre el target

variable  VIF
0                         precio_final_prom  inf
1                  numero_proyectos_activos  inf
2          Inventario_horizontal_disponible  inf
3       Creditos_otrogados_viviendas_nuevas  inf
4   Creditos_otrogados_viviendas_existentes  inf
5                           tasa_referencia  inf
6                                       PEA  inf
7                                 desempleo  inf
8                            tasa_desempleo  inf
9                                      INPC  inf
10                     Pasajeros_Nacionales  inf
11                Pasajeros_Internacionales  inf
12                    Pasajeros_5_estrellas  inf
13                    Pasajeros_4_estrellas  inf
14                    Pasajeros_3_estrellas  inf
15                    Pasajeros_2_estrellas  inf
16                  %_ocupacion_5_estrellas  inf
17                  %_ocupacion_4_estrellas  inf
18                  %_ocupacion_3_estrellas  inf
19                  %_ocupacion_2_estrellas  inf
20             Estadia_promedio_5_estrellas  inf
21             Estadia_promedio_4_estrellas  inf
22             Estadia_promedio_3_estrellas  inf
23             Estadia_promedio_2_estrellas  inf
24                Densidad_prom_5_estrellas  inf
25                Densidad_prom_4_estrellas  inf
26                Densidad_prom_3_estrellas  inf
27                Densidad_prom_2_estrellas  inf


B.1) Interpretación automática VIF
• precio_final_prom: VIF=inf → PROBLEMA: multicolinealidad extrema (VIF infinito). Elimina/combina variables.
• numero_proyectos_activos: VIF=inf → PROBLEMA: multicolinealidad extrema (VIF infinito). Elimina/combina variables.
• Inventario_horizontal_disponible: VIF=inf → PROBLEMA: multicolinealidad extrema (VIF infinito). Elimina/combina variables.
• Creditos_otrogados_viviendas_nuevas: VIF=inf → PROBLEMA: multicolinealidad extrema (VIF infinito). Elimina/combina variables.
• Creditos_otrogados_viviendas_existentes: VIF=inf → PROBLEMA: multicolinealidad extrema (VIF infinito). Elimina/combina variables.
• tasa_referencia: VIF=inf → PROBLEMA: multicolinealidad extrema (VIF infinito). Elimina/combina variables.
• PEA: VIF=inf → PROBLEMA: multicolinealidad extrema (VIF infinito). Elimina/combina variables.
• desempleo: VIF=inf → PROBLEMA: multicolinealidad extrema (VIF infinito). Elimina/combina variables.
• tasa_desempleo: VIF=inf → PROBLEMA: multicol

...


Interpretación (scatter) para 'Inventario_horizontal_disponible':
• Pearson=0.58 → Moderada positiva: relación relevante. Investigar causalidad/segmentación.
• Spearman=0.61, Kendall=0.43 → Relación aproximadamente lineal (Pearson ≈ Spearman/Kendall).
• Si el scatter muestra curvatura/saturación: prueba log(x), diferencias o modelos no lineales.
• Si sospechas rezago (preventa): prueba correlación con lag (X_{t-1}, X_{t-2}).



Interpretación (scatter) para 'Estadia_promedio_3_estrellas':
• Pearson=-0.51 → Moderada negativa: impacto importante (p.ej. sobreoferta/costo).
• Spearman=-0.42, Kendall=-0.32 → Relación aproximadamente lineal (Pearson ≈ Spearman/Kendall).
• Si el scatter muestra curvatura/saturación: prueba log(x), diferencias o modelos no lineales.
• Si sospechas rezago (preventa): prueba correlación con lag (X_{t-1}, X_{t-2}).



Interpretación (scatter) para 'Densidad_prom_5_estrellas':
• Pearson=-0.45 → Débil negativa: fricción ligera sobre el target.
• Spearman=-0.48, Kendall=-0.33 → Relación aproximadamente lineal (Pearson ≈ Spearman/Kendall).
• Si el scatter muestra curvatura/saturación: prueba log(x), diferencias o modelos no lineales.
• Si sospechas rezago (preventa): prueba correlación con lag (X_{t-1}, X_{t-2}).



Interpretación (scatter) para 'Pasajeros_Nacionales':
• Pearson=-0.44 → Débil negativa: fricción ligera sobre el target.
• Spearman=-0.39, Kendall=-0.27 → Relación aproximadamente lineal (Pearson ≈ Spearman/Kendall).
• Si el scatter muestra curvatura/saturación: prueba log(x), diferencias o modelos no lineales.
• Si sospechas rezago (preventa): prueba correlación con lag (X_{t-1}, X_{t-2}).



Interpretación (scatter) para 'tasa_referencia':
• Pearson=0.36 → Débil positiva: señal marginal. No es driver principal.
• Spearman=0.45, Kendall=0.31 → Relación aproximadamente lineal (Pearson ≈ Spearman/Kendall).
• Si el scatter muestra curvatura/saturación: prueba log(x), diferencias o modelos no lineales.
• Si sospechas rezago (preventa): prueba correlación con lag (X_{t-1}, X_{t-2}).

FIN DEL REPORTE


In [20]:
# ============================================================
# 1) CONSTRUIR ÍNDICES (ocupación / densidad / estadía / turismo)
# 2) RECALCULAR CORRELACIONES + VIF (ya NO infinitos)
# 3) ENTRENAR MODELO ARX SIMPLE CON REZAGOS y decir qué se sostiene
# ============================================================

# ============================================================
# EJECUCIÓN EN TU DF (df_ventas)
# ============================================================

# 1) Construir índices
df_idx = build_indices(df_ventas)

target = "Absorción"
reduced_features = [
    # Mercado / oferta
    "precio_final_prom",
    "Inventario_horizontal_disponible", 
    "numero_proyectos_activos",

    # Macro
    "tasa_referencia",
    "INPC",
    "tasa_desempleo",
    "PEA",

    # Índices (ya construidos)
#     "idx_turismo",
#     "idx_ocupacion",
#     "idx_estadia",
#     "idx_densidad",
]


# limpiar None y columnas inexistentes
reduced_features = [c for c in reduced_features if (c is not None and c in df_idx.columns)]

print("Features reducidas usadas:", reduced_features)

# 2) Recalcular correlaciones + VIF (ya no deberían ser infinitos)
corr_target, vif_df = corr_and_vif_report(df_idx, target=target, features=reduced_features)

print("\n=== Correlaciones vs Absorción (solo features reducidas) ===")
display(corr_target.round(3))

print("\n=== VIF (solo features reducidas) ===")
display(vif_df.round(2))

# 3) Entrenar ARX simple con rezagos
# Nota: con 16 puntos, usa pocos exógenos.
# Recomendación: 3–5 exógenos máximo.
exog_for_arx = [
    "Inventario_horizontal_disponible",
    "precio_final_prom",
    # "idx_turismo",
    # "idx_ocupacion",
    "tasa_referencia" if "tasa_referencia" in df_idx.columns else "Tasa objetivo diaria",
]
exog_for_arx = [c for c in exog_for_arx if c in df_idx.columns]

res_arx = train_arx_simple(
    df=df_idx,
    target=target,
    exog_features=exog_for_arx,
    lags_y=1,      # y_{t-1}
    lags_x=1,      # X_{t-1}
    ridge_alpha=1.0,
    n_splits=4
)

print("\n=== ARX (Abs_t ~ Abs_{t-1} + X_{t-1}) ===")
print(f"RMSE CV (TimeSeriesSplit): {res_arx['rmse_cv']:.2f}")
print(f"RMSE Fit (en-sample):     {res_arx['rmse_fit']:.2f}")
print(f"R2 Fit (en-sample):       {res_arx['r2_fit']:.3f}")

print("\n=== Coeficientes (estandarizados) — qué se sostiene ===")
display(res_arx["coef_df"])

print("\nLectura rápida:")
print("• Coeficientes con |coef| alto (impacto 'fuerte') suelen ser los drivers más estables en este ARX.")
print("• Si 'Absorción_lag1' domina, tu serie es muy autoregresiva (la inercia explica mucho).")
print("• Si 'Inventario_lag1' sale negativo fuerte, es señal de sobreoferta (consistente con teoría).")
print("• Si índices turísticos salen débiles, turismo podría ser indirecto o necesitar rezagos > 1 (lag2).")

# (Opcional) Probar también lag2 para exógenas si quieres:
# res_arx_lag2 = train_arx_simple(df_idx, target, exog_for_arx, lags_y=1, lags_x=2, ridge_alpha=1.0)
# display(res_arx_lag2["coef_df"])


Features reducidas usadas: ['precio_final_prom', 'Inventario_horizontal_disponible', 'numero_proyectos_activos', 'tasa_referencia', 'INPC', 'tasa_desempleo', 'PEA']

=== Correlaciones vs Absorción (solo features reducidas) ===


Pearson  Spearman  Kendall  |Pearson|
Inventario_horizontal_disponible    0.580     0.606    0.433      0.580
tasa_referencia                     0.362     0.447    0.308      0.362
precio_final_prom                  -0.303    -0.356   -0.300      0.303
PEA                                 0.118     0.163    0.092      0.118
tasa_desempleo                     -0.097    -0.140   -0.025      0.097
INPC                                0.071     0.157    0.126      0.071
numero_proyectos_activos            0.000     0.089    0.077      0.000


=== VIF (solo features reducidas) ===


variable   VIF
0                               PEA  6.74
1                   tasa_referencia  6.34
2                 precio_final_prom  5.23
3  Inventario_horizontal_disponible  3.64
4          numero_proyectos_activos  3.39
5                              INPC  2.04
6                    tasa_desempleo  2.03


=== ARX (Abs_t ~ Abs_{t-1} + X_{t-1}) ===
RMSE CV (TimeSeriesSplit): 31.02
RMSE Fit (en-sample):     16.63
R2 Fit (en-sample):       0.534

=== Coeficientes (estandarizados) — qué se sostiene ===


feature       coef impacto
0                 precio_final_prom_lag1 -16.622516  fuerte
1                   tasa_referencia_lag1   9.395694  fuerte
2  Inventario_horizontal_disponible_lag1   4.568318  fuerte
3                         Absorción_lag1  -3.392221  fuerte


Lectura rápida:
• Coeficientes con |coef| alto (impacto 'fuerte') suelen ser los drivers más estables en este ARX.
• Si 'Absorción_lag1' domina, tu serie es muy autoregresiva (la inercia explica mucho).
• Si 'Inventario_lag1' sale negativo fuerte, es señal de sobreoferta (consistente con teoría).
• Si índices turísticos salen débiles, turismo podría ser indirecto o necesitar rezagos > 1 (lag2).


---
---
---

In [21]:

def _infer_step_months(fecha_series: pd.Series) -> int:
    """Infere el paso temporal en meses (ej. 3 para trimestral) usando la mediana de diffs."""
    s = pd.to_datetime(fecha_series, errors="coerce").dropna().sort_values()
    if len(s) < 3:
        return 3
    diffs = s.diff().dropna()
    med_days = diffs.dt.days.median()
    if pd.isna(med_days):
        return 3
    m = int(np.round(med_days / 30.4375))
    return m if m > 0 else 3


def generar_escenarios_economicos_arx_wide(
    df: pd.DataFrame,
    modelo_arx,                         # res_arx["pipeline"]
    target: str = "Absorción",
    horizon: int = 4,
    cambios: dict | None = None,
    clip_min: float | None = 0.0        # pon None si permites negativos
) -> pd.DataFrame:
    """
    Genera escenarios de Absorción usando un modelo ARX ya entrenado (Pipeline sklearn).

    Output:
        DataFrame wide: Fecha | Conservador | Base | Optimista

    Reglas:
    - Histórico: Conservador=Base=Optimista=Absorción real.
    - Futuro: proyección iterativa (dinámica) usando Abs_{t-1}.
    - X futuro se construye usando EXACTAMENTE las columnas que el modelo espera:
      modelo_arx.feature_names_in_ (nombres + orden).

    Parámetro `cambios` (shocks % sobre el último valor observado, sostenidos en el horizonte):
        cambios = {
          "Conservador": {"precio_final_prom": +3, "idx_turismo": -6, ...},
          "Base":        {"precio_final_prom":  0, "idx_turismo":  0, ...},
          "Optimista":   {"precio_final_prom": -2, "idx_turismo": +6, ...},
        }

    Nota importante:
    - Esta función NO decide qué variables usar; usa lo que el modelo ARX fue entrenado a usar.
    - Si en `cambios` incluyes una variable que el modelo no ocupa (o no existe en df),
      se ignora silenciosamente (para evitar errores por typos o por diferencias Vertical/Horizontal).
    """

    # -----------------------------
    # 0) Preparación / validaciones
    # -----------------------------
    df = df.copy()
    if "Fecha" not in df.columns:
        raise ValueError("El DataFrame debe contener columna 'Fecha'.")
    df["Fecha"] = pd.to_datetime(df["Fecha"], errors="coerce")
    df = df.sort_values("Fecha").reset_index(drop=True)

    if target not in df.columns:
        raise ValueError(f"'{target}' no existe en df.")

    # El pipeline debe haber sido entrenado con DataFrame (para tener feature_names_in_)
    if not hasattr(modelo_arx, "feature_names_in_"):
        raise ValueError(
            "El modelo_arx no tiene feature_names_in_. "
            "Asegúrate de entrenarlo con DataFrame (no ndarray)."
        )

    feat_in = list(modelo_arx.feature_names_in_)  # nombres y orden exactos que el modelo espera

    # -----------------------------
    # 1) Inferir variables base
    #    Ej: precio_final_prom_lag1 -> precio_final_prom
    #        Absorción_lag1         -> se alimenta con y_{t-1}
    # -----------------------------
    base_vars = []
    for f in feat_in:
        if f == f"{target}_lag1":
            continue
        if f.endswith("_lag1"):
            base_vars.append(f.replace("_lag1", ""))
        else:
            base_vars.append(f)
    base_vars = sorted(set(base_vars))

    # Validar que existan en df
    faltantes = [v for v in base_vars if v not in df.columns]
    if faltantes:
        raise ValueError(
            "Faltan columnas en df para construir los features del modelo.\n"
            f"Faltantes: {faltantes}\n"
            f"El modelo espera: {feat_in}"
        )

    # -----------------------------
    # 2) Defaults de shocks (si no pasas `cambios`)
    #    (son “suaves” y genéricos; tú normalmente los pasarás explícitos)
    # -----------------------------
    if cambios is None:
        cambios = {
            "Conservador": {
                "precio_final_prom": +3,
                "idx_turismo": -6,
                "tasa_referencia": +3
            },
            "Base": {
                "precio_final_prom": 0,
                "idx_turismo": 0,
                "tasa_referencia": 0
            },
            "Optimista": {
                "precio_final_prom": -2,
                "idx_turismo": +6,
                "tasa_referencia": -3
            }
        }

    # -----------------------------
    # 3) Fechas futuras + baseline
    # -----------------------------
    step_months = _infer_step_months(df["Fecha"])
    last_date = df["Fecha"].max()
    future_dates = [last_date + pd.DateOffset(months=step_months * (i + 1)) for i in range(horizon)]

    last_row = df.iloc[-1]
    base_future = pd.DataFrame({"Fecha": future_dates})
    for v in base_vars:
        base_future[v] = last_row[v]

    # -----------------------------
    # 4) Simulación dinámica ARX por escenario
    # -----------------------------
    def _simulate_one_scenario(esc_name: str, pct_changes: dict) -> pd.Series:
        abs_prev = float(last_row[target])
        yhat = []

        for t in range(horizon):
            row = base_future.iloc[t].copy()

            # aplicar shocks % SOLO a variables base reconocidas
            for var, pct in pct_changes.items():
                if var in row.index:
                    row[var] = row[var] * (1.0 + pct / 100.0)

            # construir X exactamente como lo espera el modelo (nombres + orden)
            X_dict = {}
            for f in feat_in:
                if f == f"{target}_lag1":
                    X_dict[f] = abs_prev
                elif f.endswith("_lag1"):
                    X_dict[f] = row[f.replace("_lag1", "")]
                else:
                    X_dict[f] = row[f]

            X = pd.DataFrame([X_dict], columns=feat_in)
            abs_hat = float(modelo_arx.predict(X)[0])

            if clip_min is not None:
                abs_hat = max(clip_min, abs_hat)

            yhat.append(abs_hat)
            abs_prev = abs_hat  # dinámica autoregresiva

        return pd.Series(yhat, index=future_dates, name=esc_name)

    preds = {}
    for escenario, pct_dict in cambios.items():
        # limpiar cambios: solo llaves válidas (base_vars) para evitar errores/typos
        pct_dict = {k: v for k, v in pct_dict.items() if k in base_vars}
        preds[escenario] = _simulate_one_scenario(escenario, pct_dict)

    df_future = pd.DataFrame(preds).reset_index().rename(columns={"index": "Fecha"})

    # -----------------------------
    # 5) Histórico wide + merge
    # -----------------------------
    df_hist = df[["Fecha", target]].copy()
    df_hist["Conservador"] = df_hist[target]
    df_hist["Base"] = df_hist[target]
    df_hist["Optimista"] = df_hist[target]
    df_hist = df_hist.drop(columns=[target])

    # Unir y ordenar
    df_final = pd.concat([df_hist, df_future], ignore_index=True).sort_values("Fecha").reset_index(drop=True)
    df_final = df_final[["Fecha", "Conservador", "Base", "Optimista"]]

    return df_final


modelo = res_arx["pipeline"]

df_escenarios_h = generar_escenarios_economicos_arx_wide(
    df=df_idx,
    modelo_arx=modelo,
    target="Absorción",
    horizon=4,
    cambios = {
        "Conservador": {
            "precio_final_prom": +3,
            "idx_turismo": -6,
            "Inventario_horizontal_disponible": +2,
            "tasa_referencia": +3
        },
        "Base": {
            "precio_final_prom": 0,
            "idx_turismo": 0,
            "Inventario_horizontal_disponible": 0,
            "tasa_referencia": 0
        },
        "Optimista": {
            "precio_final_prom": -2,
            "idx_turismo": +6,
            "Inventario_horizontal_disponible": -2,
            "tasa_referencia": -3
        }
    },
    clip_min=0.0
)

df_escenarios_h

# df_escenarios_h.to_csv("Escenarios_Absorcion_Horizontal.csv", index=False)  # <- opcional


Fecha  Conservador       Base  Optimista
0  2021-12-01    36.100000  36.100000  36.100000
1  2022-03-01    21.300000  21.300000  21.300000
2  2022-08-01    84.000000  84.000000  84.000000
3  2022-11-01    64.800000  64.800000  64.800000
4  2023-02-01    70.800000  70.800000  70.800000
5  2023-05-01    91.500000  91.500000  91.500000
6  2023-08-01    42.500000  42.500000  42.500000
7  2023-11-01    47.300000  47.300000  47.300000
8  2024-02-01    43.300000  43.300000  43.300000
9  2024-05-01    19.000000  19.000000  19.000000
10 2024-08-01    28.900000  28.900000  28.900000
11 2024-11-01    79.300000  79.300000  79.300000
12 2025-02-01    40.300000  40.300000  40.300000
13 2025-05-01    36.700000  36.700000  36.700000
14 2025-08-01    12.600000  12.600000  12.600000
15 2025-11-01    25.000000  25.000000  25.000000
16 2026-02-01    17.902310  20.416117  21.577574
17 2026-05-01    18.912371  21.068442  22.064614
18 2026-08-01    18.768631  20.975611  21.995304
19 2026-11-01    18.789086  20.988821  22.005167

In [22]:


def plot_escenarios_absorcion_profesional(
    df_escenarios: pd.DataFrame,
    fecha_cutoff: pd.Timestamp | str | None = None,
    titulo: str = "Absorción Vertical — Histórico vs Escenarios (ARX)",
    subtitulo: str = "Escenarios económicos con rezagos (t-1): precio final, turismo, inventario, ocupación, tasa (proxy ciclo)",
    nota_supuestos: str | None = None,
    piso_cero: bool = False,
    show: bool = True
) -> go.Figure:
    """
    Gráfica ejecutiva profesional (Plotly) para escenarios:
    - 3 líneas (Conservador/Base/Optimista)
    - Separación Histórico vs Forecast (línea vertical + sombreado)
    - Último dato real destacado
    - Callouts (etiquetas) al final de cada escenario
    - Caja de supuestos / documentación
    """

    # ----------------------------
    # 0) Preparación
    # ----------------------------
    df = df_escenarios.copy()
    df["Fecha"] = pd.to_datetime(df["Fecha"], errors="coerce")
    df = df.sort_values("Fecha").reset_index(drop=True)

    required = {"Fecha", "Conservador", "Base", "Optimista"}
    missing = required - set(df.columns)
    if missing:
        raise ValueError(f"Faltan columnas en df_escenarios: {missing}")

    if piso_cero:
        df[["Conservador", "Base", "Optimista"]] = df[["Conservador", "Base", "Optimista"]].clip(lower=0)

    # ----------------------------
    # 1) Detectar cutoff (histórico vs forecast)
    # ----------------------------
    if fecha_cutoff is None:
        mask_hist = (df["Conservador"] == df["Base"]) & (df["Base"] == df["Optimista"])
        if mask_hist.any():
            last_hist_idx = df.index[mask_hist].max()
            fecha_cutoff = df.loc[last_hist_idx, "Fecha"]
        else:
            fecha_cutoff = df["Fecha"].iloc[-5] if len(df) > 5 else df["Fecha"].max()
    else:
        fecha_cutoff = pd.to_datetime(fecha_cutoff)

    # último dato real (toma el punto <= cutoff más cercano)
    df_cut = df[df["Fecha"] <= fecha_cutoff].tail(1)
    if df_cut.empty:
        df_cut = df.head(1)
        fecha_cutoff = df_cut["Fecha"].iloc[0]

    last_real_date = df_cut["Fecha"].iloc[0]
    last_real_val = float(df_cut["Base"].iloc[0])

    x_min = df["Fecha"].min()
    x_max = df["Fecha"].max()

    # ----------------------------
    # 2) Texto supuestos (editable)
    # ----------------------------
    if nota_supuestos is None:
        nota_supuestos = (
            "<b>Supuestos del escenario (por trimestre)</b><br>"
            "• <b>Optimista</b>: precio↓, turismo↑, inventario↓, ocupación↑<br>"
            "• <b>Base</b>: estabilidad (sin cambios relevantes)<br>"
            "• <b>Conservador</b>: precio↑, turismo↓, inventario↑, ocupación↓<br>"
            "<i>Nota:</i> ARX lineal con rezagos (t-1). Útil para simulación de decisiones; no implica causalidad."
        )

    # ----------------------------
    # 3) Figura + series
    # ----------------------------
    fig = go.Figure()

    fig.add_trace(go.Scatter(
        x=df["Fecha"], y=df["Optimista"],
        mode="lines+markers",
        name="Optimista",
        line=dict(width=3),
        marker=dict(size=7),
        hovertemplate="<b>%{x|%Y-%m-%d}</b><br>Optimista: %{y:.1f}<extra></extra>",
    ))

    fig.add_trace(go.Scatter(
        x=df["Fecha"], y=df["Base"],
        mode="lines+markers",
        name="Base",
        line=dict(width=3),
        marker=dict(size=7),
        hovertemplate="<b>%{x|%Y-%m-%d}</b><br>Base: %{y:.1f}<extra></extra>",
    ))

    fig.add_trace(go.Scatter(
        x=df["Fecha"], y=df["Conservador"],
        mode="lines+markers",
        name="Conservador",
        line=dict(width=3),
        marker=dict(size=7),
        hovertemplate="<b>%{x|%Y-%m-%d}</b><br>Conservador: %{y:.1f}<extra></extra>",
    ))

    # ----------------------------
    # 4) Sombreado forecast (shape) + línea vertical (shape)
    #    (evita add_vline/add_vrect para no chocar con Timestamp)
    # ----------------------------
    fig.add_shape(
        type="rect",
        xref="x", yref="paper",
        x0=fecha_cutoff, x1=x_max,
        y0=0, y1=1,
        fillcolor="rgba(0,0,0,0.06)",
        line_width=0,
        layer="below"
    )

    fig.add_shape(
        type="line",
        xref="x", yref="paper",
        x0=fecha_cutoff, x1=fecha_cutoff,
        y0=0, y1=1,
        line=dict(width=2, dash="dash")
    )

    # Etiquetas manuales
    fig.add_annotation(
        x=fecha_cutoff, y=1.02, xref="x", yref="paper",
        text="<b>Inicio de proyección</b>",
        showarrow=False,
        xanchor="left"
    )

    fig.add_annotation(
        x=x_max, y=1.02, xref="x", yref="paper",
        #text="Zona de escenarios (forecast)",
        # showarrow=False,
        # xanchor="right"
    )

    # ----------------------------
    # 5) Último dato real (marcador + anotación)
    # ----------------------------
    fig.add_trace(go.Scatter(
        x=[last_real_date],
        y=[last_real_val],
        mode="markers",
        name="Último dato real",
        marker=dict(size=12, symbol="diamond"),
        hovertemplate="<b>Último dato real</b><br>%{x|%Y-%m-%d}<br>Absorción: %{y:.1f}<extra></extra>",
        showlegend=True
    ))

    fig.add_annotation(
        x=last_real_date, y=last_real_val,
        text=f"Último real: <b>{last_real_val:.1f}</b>",
        showarrow=True,
        arrowhead=2,
        ax=35, ay=-25
    )

    # ----------------------------
    # 6) Callouts al final de cada escenario
    # ----------------------------
    def add_end_label(col, label, ay):
        x_end = df["Fecha"].iloc[-1]
        y_end = float(df[col].iloc[-1])
        fig.add_annotation(
            x=x_end, y=y_end,
            xanchor="left",
            text=f"<b>{label}</b>: {y_end:.1f}",
            showarrow=True,
            arrowhead=2,
            ax=45, ay=ay
        )
    add_end_label("Optimista", "Optimista", ay=-40)
    add_end_label("Base", "Base", ay=-10)
    add_end_label("Conservador", "Conservador", ay=20)

    # ----------------------------
    # 7) Layout ejecutivo + documentación
    # ----------------------------
    fig.update_layout(
        title=dict(
            text=f"<b>{titulo}</b><br><span style='font-size:13px'>{subtitulo}</span>",
            x=0.02, xanchor="left"
        ),
        xaxis=dict(
            title="Fecha",
            showgrid=True,
            ticks="outside",
            tickformat="%Y-%m"
        ),
        yaxis=dict(
            title="Absorción (unidades/mes)",
            zeroline=True,
            showgrid=True
        ),
        hovermode="x unified",
        legend=dict(
            orientation="h",
            yanchor="bottom", y=1.02,
            xanchor="left", x=0.02
        ),
        margin=dict(l=70, r=40, t=110, b=95),
        template="plotly_white",
    )

    # Caja de supuestos (debajo)
    fig.add_annotation(
        x=0.02, y=-0.28,
        xref="paper", yref="paper",
        text=nota_supuestos,
        showarrow=False,
        align="left",
        bordercolor="rgba(0,0,0,0.2)",
        borderwidth=1,
        bgcolor="rgba(255,255,255,0.90)",
        font=dict(size=12)
    )

    if show:
        fig.show()

    return fig

fig = plot_escenarios_absorcion_profesional(
    df_escenarios_h,
    piso_cero=False  # pon True si quieres recortar negativos
)

# Export opcional
# fig.write_html("Escenarios_Absorcion_Mazatlan.html", include_plotlyjs="cdn")

